# Indus Valley Script- Text Analysis for Decipherment

# Helpers and Tests

Dataset was created as a csv file from ICIT web site from raw html files of ICIT code for each for the Text
Data labels were changes and a linearized copy of the original text was added

### Input:
Pickled data file from Language Models

### Output:
Test results


!pip install numpy
!pip install pandas
!pip install matplotlib
!pip install scikit-learn
!pip install nltk
!pip install ipywidgets
!pip install -U dill
!pip3 install requests
!pip3 install -U spacy

In [1]:
import os
import time
import numpy as np
import pandas as pd
import matplotlib.pyplot as plt
from sklearn.feature_extraction.text import CountVectorizer
import nltk
import collections
import random
import traceback
import pickle

plt.style.use(style='seaborn')
%matplotlib inline

In [2]:
from nltk.util import pad_sequence
from nltk.util import bigrams
from nltk.util import ngrams
from nltk.util import everygrams
from nltk.lm.preprocessing import pad_both_ends
from nltk.lm.preprocessing import flatten
from collections import defaultdict
from nltk.lm.preprocessing import pad_both_ends
from nltk.util import everygrams
from nltk.lm.preprocessing import padded_everygram_pipeline
from nltk.tokenize import word_tokenize,sent_tokenize
from nltk.lm.models import MLE
from nltk.lm.models import KneserNeyInterpolated

In [3]:
random_seed = 8
seed = 8
CONST_INITIAL = "Initial"
CONST_TERMINAL = "Terminal"
CONST_MEDIAL = "Medial"
CONST_NL = 10

In [4]:
"""" Unpickle some of the dataframes needed """
df_train_x = pd.read_pickle('pickle/train_x.pkl')
df_train_y = pd.read_pickle('pickle/train_y.pkl')

df_train_x_rev = pd.read_pickle('pickle/train_x_rev.pkl')
df_train_y_rev = pd.read_pickle('pickle/train_y_rev.pkl')

df_test_x = pd.read_pickle('pickle/test_x.pkl')
df_test_y= pd.read_pickle('pickle/test_y.pkl')

df_test_x_rev = pd.read_pickle('pickle/test_x_rev.pkl')
df_test_y_rev = pd.read_pickle('pickle/test_y_rev.pkl')

orig_sign_df = pd.read_pickle('pickle/orig_sign_df.pkl')
print("Original sign df: \n", orig_sign_df)

df_unclear = pd.read_pickle('pickle/unclear_df.pkl')
print("Unclear text df: \n", df_unclear)

Original sign df: 
     id_sign sign_class set   graph       type        image variants  \
0         1        SIM  01  stroke     stroke  sign001.jpg        1   
1         2        MKR  01  stroke     stroke  sign002.jpg        1   
2         3        SIM  01  stroke     stroke  sign003.jpg        1   
3         4        SIM  01  stroke     stroke  sign004.jpg        1   
4         5        SIM  01  stroke     stroke  sign005.jpg        1   
..      ...        ...  ..     ...        ...          ...      ...   
704     952        CMX  71  animal  uncertain  sign952.jpg        1   
705     953        CMX  71  animal       Pict  sign953.jpg        1   
706     956        SIM  71       -    att.d.e  sign956.jpg        1   
707     957        CMX  71       -  uncertain  sign957.jpg        1   
708     958        CMX  71       -  uncertain  sign958.jpg        1   

          function ligatur value frequency comment  
0    NUM, ITM, SHN       -     -       227       -  
1    ITM, SHN, EMS   

In [5]:
model_name_list = ["MLE","KneserNeyInterpolated", "Laplace", "Lidstone","StupidBackoff", "WittenBellInterpolated"]


"""Unpickle all the trained Language Models"""
def unpickle_models(order, model_type,data_type):
    try:
        model_list= []
        for index in range (0,len(model_name_list)):
            file_name = "pickle/" + model_name_list[index]+ "_" + model_type + "_" + data_type + "_" + str(order) +".pkl"
            print("Unpickling Model from ", file_name)
            with open(file_name , 'rb') as f:
                model_list.append(pickle.load(f))
    except Exception as e:
        print("Exception:", e.__class__, "unpickle_models")
        traceback.print_exc()
    return model_list

order=1
models_list_fwd_unigram_all = unpickle_models(order,"fwd","all")
models_list_rev_unigram_all = unpickle_models(order,"rev", "all")

order=2
models_list_fwd_bigram_all = unpickle_models(order,"fwd","all")
models_list_rev_bigram_all = unpickle_models(order,"rev","all")

order=3
models_list_fwd_trigram_all = unpickle_models(order,"fwd","all")
models_list_rev_trigram_all = unpickle_models(order,"rev","all")

order=4
models_list_fwd_quadragram_all = unpickle_models(order,"fwd","all")
models_list_rev_quadragram_all = unpickle_models(order,"rev","all")

order=5
models_list_fwd_pentagram_all = unpickle_models(order,"fwd","all")
models_list_rev_pentagram_all = unpickle_models(order,"rev","all")

order=6
models_list_fwd_hexagram_all = unpickle_models(order,"fwd","all")
models_list_rev_hexagram_all = unpickle_models(order,"rev","all")

order=7
models_list_fwd_septagram_all = unpickle_models(order,"fwd","all")
models_list_rev_septagram_all = unpickle_models(order,"rev","all")

order=1
models_list_fwd_unigram = unpickle_models(order,"fwd","train")
models_list_rev_unigram = unpickle_models(order,"rev", "train")

order=2
models_list_fwd_bigram = unpickle_models(order,"fwd","train")
models_list_rev_bigram = unpickle_models(order,"rev","train")

order=3
models_list_fwd_trigram = unpickle_models(order,"fwd","train")
models_list_rev_trigram = unpickle_models(order,"rev","train")

order=4
models_list_fwd_quadragram = unpickle_models(order,"fwd","train")
models_list_rev_quadragram = unpickle_models(order,"rev","train")

order=5
models_list_fwd_pentagram = unpickle_models(order,"fwd","train")
models_list_rev_pentagram = unpickle_models(order,"rev","train")

order=6
models_list_fwd_hexagram = unpickle_models(order,"fwd","train")
models_list_rev_hexagram = unpickle_models(order,"rev","train")

order=7
models_list_fwd_septagram = unpickle_models(order,"fwd","train")
models_list_rev_septagram = unpickle_models(order,"rev","train")

Unpickling Model from  pickle/MLE_fwd_all_1.pkl
Unpickling Model from  pickle/KneserNeyInterpolated_fwd_all_1.pkl
Unpickling Model from  pickle/Laplace_fwd_all_1.pkl
Unpickling Model from  pickle/Lidstone_fwd_all_1.pkl
Unpickling Model from  pickle/StupidBackoff_fwd_all_1.pkl
Unpickling Model from  pickle/WittenBellInterpolated_fwd_all_1.pkl
Unpickling Model from  pickle/MLE_rev_all_1.pkl
Unpickling Model from  pickle/KneserNeyInterpolated_rev_all_1.pkl
Unpickling Model from  pickle/Laplace_rev_all_1.pkl
Unpickling Model from  pickle/Lidstone_rev_all_1.pkl
Unpickling Model from  pickle/StupidBackoff_rev_all_1.pkl
Unpickling Model from  pickle/WittenBellInterpolated_rev_all_1.pkl
Unpickling Model from  pickle/MLE_fwd_all_2.pkl
Unpickling Model from  pickle/KneserNeyInterpolated_fwd_all_2.pkl
Unpickling Model from  pickle/Laplace_fwd_all_2.pkl
Unpickling Model from  pickle/Lidstone_fwd_all_2.pkl
Unpickling Model from  pickle/StupidBackoff_fwd_all_2.pkl
Unpickling Model from  pickle/Witte

Unpickling Model from  pickle/KneserNeyInterpolated_fwd_train_6.pkl
Unpickling Model from  pickle/Laplace_fwd_train_6.pkl
Unpickling Model from  pickle/Lidstone_fwd_train_6.pkl
Unpickling Model from  pickle/StupidBackoff_fwd_train_6.pkl
Unpickling Model from  pickle/WittenBellInterpolated_fwd_train_6.pkl
Unpickling Model from  pickle/MLE_rev_train_6.pkl
Unpickling Model from  pickle/KneserNeyInterpolated_rev_train_6.pkl
Unpickling Model from  pickle/Laplace_rev_train_6.pkl
Unpickling Model from  pickle/Lidstone_rev_train_6.pkl
Unpickling Model from  pickle/StupidBackoff_rev_train_6.pkl
Unpickling Model from  pickle/WittenBellInterpolated_rev_train_6.pkl
Unpickling Model from  pickle/MLE_fwd_train_7.pkl
Unpickling Model from  pickle/KneserNeyInterpolated_fwd_train_7.pkl
Unpickling Model from  pickle/Laplace_fwd_train_7.pkl
Unpickling Model from  pickle/Lidstone_fwd_train_7.pkl
Unpickling Model from  pickle/StupidBackoff_fwd_train_7.pkl
Unpickling Model from  pickle/WittenBellInterpolate

In [6]:
"""Unpickle the Initial Terminal KnesserNey Bigram model"""
file_name = "pickle/KneserNeyInterpolated_it_2.pkl"
print("Unpickling Model from ", file_name)
with open(file_name , 'rb') as f:
    model_it_bigram_kn = pickle.load(f)

Unpickling Model from  pickle/KneserNeyInterpolated_it_2.pkl


In [7]:
def reverse_text(text):
    # first split the string into chars
    chars = text.split(' ')

    # then reverse the split string list and join with a space
    reversed_text = ' '.join(reversed(chars))
    return reversed_text

In [8]:
def reverse_single_text(text):
    list_reversed_text = []
    # Tokenize to words
    # first split the string into chars
    chars = text.split(' ')

    # then reverse the split string list and join with a space
    reversed_text = ' '.join(reversed(chars))
    return reversed_text

In [9]:
def reverse_text(a):
    list_reversed_text = []
    for text in a :
        # Tokenize to words
        # first split the string into chars
        chars = text.split(' ')

        # then reverse the split string list and join with a space
        reversed_text = ' '.join(reversed(chars))
        list_reversed_text.append(reversed_text)
    return list_reversed_text 

In [10]:
# Get ngram as list given a text (pass direction_of_string as "R/L" or "L/R")
def get_ngrams_as_list(data,direction_of_string,num):
    
    if(direction_of_string=="R/L"):
        # We need to convert R/L text to L/R to be able to get ngrams using nltk
        data_string = reverse_text(data)
    
    else: data_string= data
    
    n_grams =  ngrams(nltk.word_tokenize(data_string), num)
    return  [ ' '.join(grams) for grams in n_grams]

# Text Positional Ngram Analysis Model

In [11]:
from nltk.tokenize import word_tokenize,sent_tokenize
from typing import Dict
from bisect import bisect
from itertools import accumulate

class PositionalNgramModel:
    text_norm_position_unigrams_freq_dict=None
    df_text_norm_position_unigrams_freq=None
    df_text_norm_position_unigrams_prob=None
    text_norm_position_unigrams_maxValueIndex_dict = None
    text_norm_position_unigrams_unigrams_tuple = ()
    
    text_norm_position_bigrams_freq_dict = None
    df_text_norm_position_bigrams_freq=None
    df_text_norm_position_bigrams_prob=None
    text_norm_position_bigrams_maxValueIndex_dict = None
    
    text_norm_position_trigrams_freq_dict = None
    df_text_norm_position_trigrams_freq=None
    df_text_norm_position_trigrams_prob=None
    text_norm_position_trigrams_maxValueIndex_dict = None
    
    text_norm_position_quadgrams_freq_dict= None
    df_text_norm_position_quadgrams_freq=None
    df_text_norm_position_quadgrams_prob=None
    text_norm_position_bigrams_maxValueIndex_dict = None
    

    def _random_generator(self, seed_or_generator):
        if isinstance(seed_or_generator, random.Random):
            return seed_or_generator
        return random.Random(seed_or_generator)
    
    def _weighted_choice(self, population, weights, random_generator=None):
        """Like random.choice, but with weights.
        Heavily inspired by python 3.6 `random.choices`.
        """
        if not population:
            raise ValueError("Can't choose from empty population")
        if len(population) != len(weights):
            raise ValueError("The number of weights does not match the population")
        cum_weights = list(accumulate(weights))
        total = cum_weights[-1]
        threshold = random_generator.random()
        return population[bisect(cum_weights, total * threshold)]
    
    # To get a Positional Number for a unigram, bigram, trigram and Quadgram
    # l = Length of the text
    # s = starting position of the first character of the ngram
    # wp = weighted position = int(s/l)
    # Get the normalized position
    # Since the text passed is L/R,start index i from length of the text
    def get_norm_position(self, text,direction_of_string, search_string):
        try:
            num_chars, minp, maxp,w = 0,-1,-1,0
            sp=-1
            index=-1
            pos=-1

            #ngrams which are used as search_strings are generated from left to right, so text need to be changed to L/R

            if(direction_of_string=="R/L"):
                new_text = reverse_text(text)
            else: new_text = text


            l_pos= len(new_text )

            chars = new_text .split(' ')
            num_chars = len(chars)
            w= num_chars/CONST_NL


            pos = new_text.find(search_string)
            if(pos<0):  #not found
                return sp, minp, maxp, w
            else: 
                #sp = round((l_pos-pos)/4)
                sp = round(pos/4 +1)

            minp= int((sp-1)* (CONST_NL/num_chars) +1)
            maxp = int(sp*CONST_NL/num_chars)

            #print("text, search_string", new_text ,",", search_string)
            #print("l_pos, pos, sp, minp, maxp", l_pos, pos,sp, minp, maxp)

            if(minp<1): minp=1
            elif(minp>CONST_NL): minp = CONST_NL

            if(maxp<1): maxp=1
            elif(maxp>CONST_NL): maxp = CONST_NL

        except Exception as e:
            print("Exception:", e.__class__, "get_norm_position")
            traceback.print_exc()

        return sp,minp, maxp, w


    def get_text_norm_position_ngrams_freq(self,a,direction_of_string, n):

        average_allocation= True # Average out minp and maxp and allocate to the histogram. Don't care about weight

        text_norm_position_ngrams_freq=defaultdict(dict[int, int])
        norm_pos =-1
        i=0
        sp=-1

        try:
            #Fill the values with zeros in decreasing order so that we can keep same order in graph
            for text in a:
              for word in get_ngrams_as_list(text,direction_of_string, n):
                for j in range (10,0, -1):
                    text_norm_position_ngrams_freq[word][j]=0

            for text in a:
              for word in get_ngrams_as_list(text,direction_of_string, n):
                initial_char = word #Look for position of Initial char of the ngram
                sp,minp, maxp, w = self.get_norm_position(text,direction_of_string, initial_char)

                if(minp<0 or maxp<0): break #No match


                if(average_allocation):
                    norm_pos = round((minp+ maxp)/2)
                    #print("word, norm_pos", word, norm_pos)
                    val = text_norm_position_ngrams_freq[word].get(norm_pos,0)
                    text_norm_position_ngrams_freq[word][norm_pos]= val+ w
                else:

                    if(minp!=maxp):
                        val = text_norm_position_ngrams_freq[word].get(minp,0)
                        text_norm_position_ngrams_freq[word][minp]= val+ w

                        val = text_norm_position_ngrams_freq[word].get(maxp,0)
                        text_norm_position_ngrams_freq[word][maxp]= val +w
                    else:
                        val = text_norm_position_ngrams_freq[word].get(minp,0)
                        text_norm_position_ngrams_freq[word][minp]= val+ w

                #if(initial_char=="740"): print(i,":Text:",text, "Char", initial_char, "sp, minp, maxp, w, norm_pos", sp, minp, maxp, w, norm_pos)

                #if(initial_char=="817 002"): print(i,":Text:",text, "Char:", initial_char, sp, minp, maxp, w, norm_pos)

                i=i+1

        except Exception as e:
                print("Exception:", e.__class__, "get_text_norm_position_ngrams_freq")
                traceback.print_exc()

        return  text_norm_position_ngrams_freq

    # Can be generatilzed to any N later
    def fit(self, a, direction_of_string):
        try:
            print(a)

            self.text_norm_position_unigrams_freq_dict=defaultdict(dict[int, int])
            self.text_norm_position_unigrams_freq_dict=self.get_text_norm_position_ngrams_freq(a,direction_of_string, 1)
            self.df_text_norm_position_unigrams_freq=pd.DataFrame(self.text_norm_position_unigrams_freq_dict)

            self.df_text_norm_position_unigrams_prob = self.df_text_norm_position_unigrams_freq.div(self.df_text_norm_position_unigrams_freq.sum(axis=1), axis=0)
            self.df_text_norm_position_unigrams_prob = self.df_text_norm_position_unigrams_prob.assign(max_value=self.df_text_norm_position_unigrams_prob.values.max(1))
            df_text_norm_position_unigrams_maxValueIndex = self.df_text_norm_position_unigrams_prob.idxmax(axis = 1)
            self.text_norm_position_unigrams_maxValueIndex_dict = df_text_norm_position_unigrams_maxValueIndex.to_dict()

            # Build the unigrams tuple
            for col in self.df_text_norm_position_unigrams_prob:
                self.text_norm_position_unigrams_unigrams_tuple =  self.text_norm_position_unigrams_unigrams_tuple + (col,)

            self.text_norm_position_unigrams_unigrams_tuple= sorted(self.text_norm_position_unigrams_unigrams_tuple)

            #print(self.df_text_norm_position_unigrams_freq)
            #print(self.df_text_norm_position_unigrams_prob)
            #print(self.text_norm_position_unigrams_maxValueIndex_dict)

            #Bigram
            self.text_norm_position_bigrams_freq_dict=defaultdict(dict[int, int])
            self.text_norm_position_bigrams_freq_dict=self.get_text_norm_position_ngrams_freq(a,direction_of_string,2)
            self.df_text_norm_position_bigrams_freq=pd.DataFrame(self.text_norm_position_bigrams_freq_dict)
            self.df_text_norm_position_bigrams_prob = self.df_text_norm_position_bigrams_freq.div(self.df_text_norm_position_bigrams_freq.sum(axis=1), axis=0)
            #print(self.df_text_norm_position_bigrams_freq)test

            #Trigram
            self.text_norm_position_trigrams_freq_dict=defaultdict(dict[int, int])
            self.text_norm_position_trigrams_freq_dict=self.get_text_norm_position_ngrams_freq(a,direction_of_string,3)
            self.df_text_norm_position_trigrams_freq=pd.DataFrame(self.text_norm_position_trigrams_freq_dict)
            self.df_text_norm_position_trigrams_prob = self.df_text_norm_position_trigrams_freq.div(self.df_text_norm_position_trigrams_freq.sum(axis=1), axis=0)
            #print(self.df_text_norm_position_trigrams_freq)

            #Quadgram
            self.text_norm_position_quadgrams_freq_dict=defaultdict(dict[int, int])
            self.text_norm_position_quadgrams_freq_dict=self.get_text_norm_position_ngrams_freq(a,direction_of_string,4)
            self.df_text_norm_position_quadgrams_freq=pd.DataFrame(self.text_norm_position_quadgrams_freq_dict)
            self.df_text_norm_position_quadgrams_prob = self.df_text_norm_position_quadgrams_freq.div(self.df_text_norm_position_quadgrams_freq.sum(axis=1), axis=0)
            #print(df_text_norm_position_quadgrams_freq)
        
        except Exception as e:
            print("Exception:", e.__class__, "fit")
            traceback.print_exc()
        
        return self.df_text_norm_position_unigrams_prob, self.df_text_norm_position_bigrams_prob, self.df_text_norm_position_trigrams_prob,self.df_text_norm_position_quadgrams_prob

    def get_text_norm_position_unigrams_char_with_max_prob(self, position):
        try:
            char= self.text_norm_position_unigrams_maxValueIndex_dict[position]
            print("Max Prob for Position:", position, "is for character:",char )
        
        except Exception as e:
            print("Exception:", e.__class__, "get_text_norm_position_unigrams_char_with_max_prob")
            traceback.print_exc()
        return char
    
    def get_text_norm_position_unigrams_char_prob(self, position, word):
       
        prob=0
        try:
            prob = self.df_text_norm_position_unigrams_prob.loc[position,word]
        except Exception as e:
            print("Exception:", e.__class__, "get_text_norm_position_unigrams_char_prob")
            traceback.print_exc()
        return prob
    
    def get_text_norm_position_unigrams_char_with_weighted_prob(self, position):

        try:
            random_generator = self._random_generator(random_seed)
            #print(tuple(self.get_text_norm_position_unigrams_char_prob(position, w) for w in  self.text_norm_position_unigrams_unigrams_tuple)) 

            return self._weighted_choice(
                    self.text_norm_position_unigrams_unigrams_tuple,
                    tuple(self.get_text_norm_position_unigrams_char_prob(position, w) for w in  self.text_norm_position_unigrams_unigrams_tuple),
                    random_generator,
                )
        except Exception as e:
            print("Exception:", e.__class__, "get_text_norm_position_unigrams_char_with_weighted_prob")
            traceback.print_exc()
    
    def find_characters(self, a, seed):
        #For each of the text with unclear character go through it
        ans=-1
        out_char = None
        out_char_list = []
        try:
            for text in a :
                print("Finding Unclear character for", text)
                chars = text.split(' ')
                index = len(chars) - chars.index("000")
                if(index<0):  #not found
                    return 
                else: 
                    # Find the char with highest probablity for this position
                    print(index)
                    out_char = self.get_text_norm_position_unigrams_char_with_max_prob(index)
                    print("Index, out_char:", index, out_char)
                    out_char_list.append(out_char)
    
        except Exception as e:
            print("Exception:", e.__class__, "find_characters")
            
        return  out_char_list

## Text Positional Analysis - Basic check

In [12]:
a= df_train_x[df_train_x.l_to_r_text!=''].l_to_r_text
posNgramModel = PositionalNgramModel()

#Train model with xtrain data
df_text_norm_position_unigrams_prob, df_text_norm_position_bigrams_prob, df_text_norm_position_trigrams_prob,df_text_norm_position_quadgrams_prob = posNgramModel.fit(a, "L/R")

#print(posNgramModel.get_text_norm_position_unigrams_char_prob(10, '720'))

print(posNgramModel.get_text_norm_position_unigrams_char_with_weighted_prob(1))
print(posNgramModel.get_text_norm_position_unigrams_char_with_weighted_prob(10))

0                             817 002 013 840 176 100 740
1                                         125 384 700 875
2       140 919 520 360 861 002 235 231 705 033 032 87...
3                                                 818 002
4                             032 590 741 350 460 798 740
                              ...                        
1995                                      240 100 740 400
1996                                      840 032 740 400
1997                                      370 002 550 527
1998                                      235 220 222 740
1999                              820 002 803 032 384 740
Name: l_to_r_text, Length: 2000, dtype: object
235
409


## ModelWithFilling for ngram

In [13]:
from bisect import bisect
from itertools import accumulate
from nltk.tokenize.treebank import TreebankWordDetokenizer
import traceback

detokenize = TreebankWordDetokenizer().detokenize 

class ModelWithFilling:

    def __init__(self, this_model, posNgramModel=None, fill_using_position=True):
        self.model = this_model
        self.posNgramModel = posNgramModel
        self.fill_using_position = fill_using_position
        if(not this_model or not posNgramModel): print("Need non Empty Model for creating instance of ModelWithFilling")
        
    def _random_generator(self, seed_or_generator):
        if isinstance(seed_or_generator, random.Random):
            return seed_or_generator
        return random.Random(seed_or_generator)
    
    def _weighted_choice(self, population, weights, random_generator=None):
        """This is from NLTK """
        """Like random.choice, but with weights.
        Heavily inspired by python 3.6 `random.choices`.
        """
        if not population:
            raise ValueError("Can't choose from empty population")
        if len(population) != len(weights):
            raise ValueError("The number of weights does not match the population")
        cum_weights = list(accumulate(weights))
        total = cum_weights[-1]
        threshold = random_generator.random()
        #TBD Remove this
        #threshold =0.001
        
        return population[bisect(cum_weights, total * threshold)]

        
    def get_model(self):
        return self.model

    
      # Redefine this function defined in NTLK with some changes
    def generate(self,num_words=1, text_seed=None, random_seed=None, position=-1):

        #print("Generating for text:", text_seed, "and position:", position)
        text_seed = [] if text_seed is None else list(text_seed)
        pos=-1

        random_generator = self._random_generator(random_seed)
        # This is the base recursion case.
        if num_words == 1:
            context = (
                text_seed[-self.model.order + 1 :]
                if len(text_seed) >= self.model.order
                else text_seed
            )
            samples = self.model.context_counts(self.model.vocab.lookup(context))   
            
            #print("____Context:", context, "Samples:", samples)
            while context and not samples:
                context = context[1:] if len(context) > 1 else []
                samples = self.model.context_counts(self.model.vocab.lookup(context))
            # Sorting samples achieves two things:
            # - reproducible randomness when sampling
            # - turns Mapping into Sequence which `_weighted_choice` expects
            samples = sorted(samples)
            
            #if(len(context) < 1 ): 
                #print("@@@@@@@@@@@@@@@@@@@@@@@", "context:", context, "Must return Positional Prob for pos:", position)
                
            if(self.fill_using_position and self.posNgramModel and len(context)<1 and position!=-1):
                pos = self.posNgramModel.get_text_norm_position_unigrams_char_with_weighted_prob(position)
                print("Returning Positional Prob for pos:", position, ":", pos, "for text_seed:", text_seed)
                return pos
            else: 
                #print("Before returning, Context:", context)
                #for w in samples:
                    #print("Before returning, Sample Item:", w, self.model.score(w, context))
                    
                return self._weighted_choice(
                samples,
                tuple(self.model.score(w, context) for w in samples),
                random_generator,
            )
        
        # We build up text one word at a time using the preceding context.
        generated = []
        for _ in range(num_words):
            generated.append(
                self.generate(
                    num_words=1,
                    text_seed=text_seed + generated,
                    random_seed=random_generator,
                )
            )
        return generated
    

    def generate_sent(self, num_words,char_seed, random_seed, position=-1):
        """
        :param model: An ngram language model.
        :param num_words: Max no. of words to generate.
        :param random_seed: Seed value for random.
        """
        content = []
        try:
            for token in self.generate(num_words, text_seed=char_seed, random_seed=random_seed, position=position):
                if token == '<s>':
                    continue
                if token == '</s>'  or token == '< /s>' :
                    break
                content.append(token)
        except Exception as e:
            print("Exception:", e.__class__, "in ModelwithFilling:generate_sent")
            traceback.print_exc()
        return detokenize(content)
    
     # Redefine this function defined in NTLK with some changes
    def generate0(self,scores_dict, num_words=1, text_seed=None, random_seed=None, position=-1):
    
        try:
            #print("Generating for text:", text_seed, "and position:", position)
            text_seed = [] if text_seed is None else list(text_seed)
            pos=-1

            random_generator = self._random_generator(random_seed)
            # This is the base recursion case.
            if num_words == 1:
                context = (
                    text_seed[-self.model.order + 1 :]
                    if len(text_seed) >= self.model.order
                    else text_seed
                )
                samples = self.model.context_counts(self.model.vocab.lookup(context))
                
                #Added: If we get a padding character, ignore it and go further
                if(len(samples)==1):
                    #print(samples)
                    for w in samples:
                        if(w=="</s>" or w=="<s>" ): 
                            #print("settings samples to None")
                            samples = None
                    

                #print("____Context:", context, "Samples:", samples)
                while context and not samples:
                    context = context[1:] if len(context) > 1 else []
                    samples = self.model.context_counts(self.model.vocab.lookup(context))
                # Sorting samples achieves two things:
                # - reproducible randomness when sampling
                # - turns Mapping into Sequence which `_weighted_choice` expects
                samples = sorted(samples)

                #if(len(context) < 1 ): 
                    #print("@@@@@@@@@@@@@@@@@@@@@@@", "context:", context, "Must return Positional Prob for pos:", position)

                if(self.fill_using_position and self.posNgramModel and len(context)<1 and position!=-1):
                    pos = self.posNgramModel.get_text_norm_position_unigrams_char_with_weighted_prob(position)
                    print("Returning Positional Prob for pos:", position, ":", pos, "for text_seed:", text_seed)
                    return pos
                else: 
                    #print("Before returning, Context:", context)
                    for w in samples:
                        scr = self.model.score(w, context)
                        scores_dict[w]=scr
                        #print("Context:", context, "sample",w, "score", scr)


                    return self._weighted_choice(
                    samples,
                    tuple(self.model.score(w, context) for w in samples),
                    random_generator,
                ), scores_dict, context #sending the scores dictionary

            # We build up text one word at a time using the preceding context.
            generated = []
            for _ in range(num_words):
                generated.append(
                    self.generate0(
                        scores_dict,
                        num_words=1,
                        text_seed=text_seed + generated,
                        random_seed=random_generator,
                    )
                )
        except Exception as e:
            print("Exception:", e.__class__, "in generate0")
            traceback.print_exc()
            
        return generated,scores_dict, context #sending the dictionary and the context
    
    def generate_sent0(self, num_words,char_seed, random_seed, position=-1):
        """
        :param model: An ngram language model.
        :param num_words: Max no. of words to generate.
        :param random_seed: Seed value for random.
        """
        content = []
        token_list = []
        #dict to store score of various options we had
        scores_dict = defaultdict() # Pass it in
        try:
            token_list, scores_dict, context = self.generate0(scores_dict, num_words, text_seed=char_seed, random_seed=random_seed, position=position)
            # clean dictionary of padding
            scores_dict.pop('<s>', None)
            scores_dict.pop('</s>', None)
            scores_dict.pop('< /s>', None)
            
            for token in token_list:
                if token == '<s>':
                    continue
                if token == '</s>'  or token == '< /s>' :
                    break
                content.append(token)
        except Exception as e:
            print("Exception:", e.__class__, "in ModelwithFilling:generate_sent0")
            traceback.print_exc()
        return detokenize(content), scores_dict, context
    
    def get_the_perplexity(self, text, sign):
        
        perp_dict = defaultdict()
        perp=100000
        #this_tokenized_text= word_tokenize(text)
        this_tokenized_text= text.split(' ')
        this_tokenized_text_list = []
        this_tokenized_text_list.append(this_tokenized_text)

        #print("this_tokenized_text_list", this_tokenized_text_list)
        this_data_list = []
        this_data_list, _= padded_everygram_pipeline(self.model.order, this_tokenized_text_list)
        for i, test in enumerate(this_data_list):
            perp =self.model.perplexity(test)
            if(perp>100000): perp = 100000

            #if(perp<100000):print("sign:",sign, "text:", new_text,"Perp:", perp)
            perp_dict[str(sign)] = perp 
        
        min_value = min(perp_dict.values())
        res = [key for key in perp_dict if perp_dict[key] == min_value]
        #print("res[0], min_value", res[0], min_value)
                
        return res[0], min_value
    
    
    def get_model_ngrams_list_for_missing_ends(self, context_text_token_list, position_missing):
        try:
            list_ngrams = []
            list_dict_ngrams= []
            k= len(context_text_token_list)
            init_char_missing,final_char_missing= False, False
            
            """If k is greater than order of the model return none"""
            if(k>self.model.order): return list_ngrams
        
            """ Get the ngrams of order k+1: This is assuming padding is sent in the text"""
            """ If model order is < k then an empty list is returned"""
            list_dict_ngrams = list(self.model.counts[k+1])
            #print("Input context:", context_text_token_list)
            #print("List of ngrams of order ", k, ":", list_dict_ngrams)
            
            if(position_missing=="initial"): init_char_missing = True
            elif(position_missing=="terminal"): final_char_missing = True
            
            for tpl in list_dict_ngrams:
                """ There won't be any match if number of items in tpl is not same as k """
                """ which will happen if context is longer than order of the model"""
                if(len(tpl)==k):
                    #print("text_list, tpl:", context_text_token_list, tpl)
                    
                    """Do a match and append the matched tpls to list_ngrams"""
                    
                    if(init_char_missing):
                        match= True
                        if(context_text_token_list[0]==tpl[0]):
                            
                            """Skip the second char, start from third char till the end"""
                            for m in range(2, len(context_text_token_list)):        
                                if(context_text_token_list[m]!=tpl[m]):
                                    match = False
                                    break
                            if(match): 
                                if(init_char_missing):
                                    """Append the second element of the tuple"""
                                    """ Don't match <s> and </s>"""
                                    if(tpl[1]!="<s>" and tpl[1]!="</s>"): 
                                        #print("######## Matched! Adding",tpl[1])
                                        list_ngrams.append(tpl[1])
                                        
                    elif(final_char_missing):
                        match= True
                        last_char_context = len(context_text_token_list)-1
                        last_char_tpl = len(tpl)-1
                        
                        if(context_text_token_list[last_char_context]==tpl[last_char_tpl]):
                            
                            """Start from beginning, to the char before missing char"""
                            for m in range(0, last_char_context-1):    
                                #print("--Comparing",context_text_token_list[m],tpl[m])
                                if(context_text_token_list[m]!=tpl[m]):
                                    match = False
                                    break

                            if(match): 
                                if(final_char_missing):
                                    """Append the last but one element of the tuple"""
                                    """ Don't match <s> and </s>"""
                                    if(tpl[last_char_tpl-1]!="<s>" and tpl[last_char_tpl-1]!="</s>"): 
                                        #print("######## Matched! Adding",tpl[last_char_tpl-1])
                                        list_ngrams.append(tpl[last_char_tpl-1])
                            
                            
        except Exception as e:
            print("Exception:", e.__class__, "get_model_ngrams_list_for_missing_ends")
            traceback.print_exc()    
        return list_ngrams
            
        
    """ From the language model get the k th order ngram
        and using it get the characters that form the ngram"""
    def get_model_ngrams_list0(self, text, k, type_ngram):
        try:
            list_ngrams = []
            list_dict_ngrams = list(self.model.counts[k+1])
            
            #print("get_model_ngrams_list0", text, ":", list_dict_ngrams)

            if(k>=3):
                # cannot use word_tokenize as we could be dealing with <s>
                text_list = text.split(' ')

            for tpl in list_dict_ngrams:

                if(k==2 and len(tpl)>1):
                    #bigram
                    if(type_ngram=="left_bigram" and tpl[0]==text):
                        list_ngrams.append(tpl[1])
                    elif(type_ngram=="right_bigram" and tpl[1]==text):

                        list_ngrams.append(tpl[0])

                elif(k==3 and len(tpl)>2):
                    #trigram
                    if(type_ngram=="trigram" and tpl[0]==text_list[0] and tpl[2]==text_list[1]):
                        list_ngrams.append(tpl[1])
                elif(k==4 and len(tpl)>3):
                    #quadragram
                    #print("text_list, tpl:", text_list, tpl)
                    if(type_ngram=="quadragram" and tpl[0]==text_list[0] and tpl[2]==text_list[1] and tpl[3]==text_list[2]):
                        list_ngrams.append(tpl[1])

        except Exception as e:
            print("Exception:", e.__class__, "get_model_ngrams_list0")
            traceback.print_exc()    
        return list_ngrams
  
    
    def get_the_score(self, text):
        
        try:
            score =0
            #list_tokens = nltk.word_tokenize(text)
            
            # cannot use word_tokenize as we could be dealing with <s>
            list_tokens = text.split(' ')
            #print("list_tokens:", list_tokens)
            if(len(list_tokens)==1):
                score = self.model.score(list_tokens[0]) 
            elif(len(list_tokens)==2):
                score = self.model.score(list_tokens[1], list_tokens[0].split())
            elif(len(list_tokens)==3):
                score = self.model.score(list_tokens[2], (list_tokens[0] + " " + list_tokens[1]).split())
            elif(len(list_tokens)==4):
                score = self.model.score(list_tokens[3], (list_tokens[0] + " " + list_tokens[1] + " " + list_tokens[2]).split())
            elif(len(list_tokens)==5):
                score = self.model.score(list_tokens[4], (list_tokens[0] + " " + list_tokens[1] + " " + list_tokens[2] + " " + list_tokens[3]).split())
            elif(len(list_tokens)==6):
                score = self.model.score(list_tokens[5], (list_tokens[0] + " " + list_tokens[1] + " " + list_tokens[2] + " " + list_tokens[3] + " " + list_tokens[4]).split())
            elif(len(list_tokens)==7):
                score = self.model.score(list_tokens[6], (list_tokens[0] + " " + list_tokens[1] + " " + list_tokens[2] + " " + list_tokens[3] + " " + list_tokens[4] + " " + list_tokens[5]).split())
            else:
                print("More than 7 tokens in input text. Not getting score",list_tokens )
        except Exception as e:
            print("Exception:", e.__class__, "get_the_score")
            traceback.print_exc()
        return score
    
    def compute_score(self, list_ngram, char1, char2,char3, type_ngram):
        
        try:
            score =0
            this_dict = defaultdict()
            
            #print("compute_score:", type_ngram, list_ngram)
            
            #print("Getting compute_score for:", type_ngram)

            for sign in list_ngram:

                if(sign!='<s>'): replaced_sign = f"{sign:03}"
                else: replaced_sign = sign

                if(type_ngram=="left_bigram"):
                    left_bigram = char1 + " " + replaced_sign
                    score = self.get_the_score(left_bigram)
                    this_dict[replaced_sign]=score

                elif(type_ngram=="right_bigram"):
                    right_bigram = replaced_sign + " " + char1
                    score = self.get_the_score(right_bigram)
                    this_dict[replaced_sign]=score

                elif(type_ngram=="trigram"):
                    trigram = char1 + " " + replaced_sign +  " " + char2
                    score = self.get_the_score(trigram)
                    this_dict[replaced_sign]=score
                    
                elif(type_ngram=="quadragram"):
                    quadragram = char1 + " " + replaced_sign +  " " + char2 + " " + char3
                    #print("Getting quadragram score for:", quadragram)
                    score = self.get_the_score(quadragram)
                    this_dict[replaced_sign]=score
                else:
                    print("Wrong type ngram. Can't compute score")

        except Exception as e:
            print("Exception:", e.__class__, "compute_score")
            traceback.print_exc()

        return this_dict

    """ Dictionary passed in has the char and score
         match the character in dictionaries and get score and calculate
         ranks.Return a rank dictionary with charactor and score"""
    def get_char_and_rank(self, dict1, dict2):

        alpha1=0.5
        alpha2=0.5
        score1, score2 = 0,0
        rank=0
        rank_dict = defaultdict()
        full_list = []
        
        try:
            """ For Initial character dict2 will be empty"""
            if(dict1==None and dict2):
                alpha1=0
                alpha2=1
            elif(dict2 and dict2==None):
                alpha1=1
                alpha2=0
        
            #create a list of keys with no duplicates in a list
            if(dict1): full_list = list(dict1.keys())
            if(dict2): full_list = list(set(full_list + list(dict2.keys())))

            for sign in full_list:
                if(sign!='<s>' or sign!='</s>' ): replaced_sign = f"{sign:03}"
                else: replaced_sign = sign

                if dict1 and replaced_sign in dict1:
                    score1 = dict1[replaced_sign]
                else: score1=0

                if dict2 and replaced_sign in dict2:
                    score2 = dict2[replaced_sign]
                else: score2=0

                rank = alpha1*score1  + alpha2*score2
                rank_dict[replaced_sign]=rank

            sorted_rank_list = sorted(rank_dict.items(),reverse=True, key=lambda x:x[1])
            
            #if(len(sorted_rank_list)==0): 
                #print("dict1:", dict1, "dict2:", dict2, "full_list:", full_list)
                #print("alpha1:", alpha2, "alpha2:, alpha2")
                      
            #print("Sorted Rank --------:", sorted_rank_list)
            if(len(sorted_rank_list)>0):
                sign_rank_tpl = sorted_rank_list[0]
                return sign_rank_tpl[0], sign_rank_tpl[1]
            else:
                """Sorted rank list has no elements, returning nothing"""
                #print("dict1:", dict1, "\n" "dict2:", dict2)
                return None, -1
        
        except Exception as e:
            print("Exception:", e.__class__, "get_char_and_rank")
            traceback.print_exc()
            
        return None, -1

    
    """ This is to find the missing characters
    If the missing character is found in ith position in the text and text is of length m,
    start with finding 1 ngram of size 1, 2 ngram of size m-1 until you reach 1 ngram of size 1
    While doing it, for each of the ngram, identify the best fit character that gives the best model score. 
    Character identified by highest order ngram wins."""
    
    def get_missing_char(self,text, random_seed=seed, position=-1):
        
        missing_char=""
        sign_score =-1
        order_of_match=-1
        i=-1
        result_list = []
        fetch_all_highest_order_results=True
        try:
            text_ngrams_list = []
            list_tokens = text.split(' ')
            last_token_index = len(list_tokens)-1 
            
            i = list_tokens.index("000") if "000" in list_tokens else None             
            if(i==None): 
                print("Text does not have missing character!")
                return missing_char, sign_score, order_of_match, result_list
                
            for char_idx in range(0, i+1):
                for n in range(last_token_index+1, i, -1):
                    list_to_add = list_tokens[char_idx:n]
                    """ No point searching for the whole text in the model, as
                    it would give you a hit for all items in train data.So ignore that"""
                    if(len(list_to_add) != len(list_tokens)):
                        #TBD remove this if condition later
                        #if('<s>' not in list_to_add and '</s>' not in list_to_add):
                            text_ngrams_list.append(list_to_add)
            
            """Sort by length of ngram descending"""
            text_ngrams_list.sort(key=len, reverse=True)
            #print("text_ngrams_list:", text_ngrams_list)
            
            """send the list token and list of list of ngram to get an answer"""
            result_list = self.get_missing_char_selection(text_ngrams_list, fetch_all_highest_order_results)
            
            if(result_list):
                """ get the result among all the results with highest sign_score and return that"""
                for j in range(0, len(result_list)):
                    if(result_list[j][2]>=sign_score):
                        idx = j
                        sign_score = result_list[j][2]
                
                result_context_list= result_list[idx][0] 
                missing_char = result_list[idx][1] 
                sign_score = result_list[idx][2]
                order_of_match = result_list[idx][3]
            
        except Exception as e:
            print("Exception:", e.__class__, "get_missing_char")
            traceback.print_exc()
        return missing_char, sign_score, order_of_match, result_list

    
    def get_missing_char_selection(self,text_ngrams_list, fetch_all_highest_order_results=False):
  
        try:
            score_dict = defaultdict()
            result_list = []
            order_of_match=0
            sign_score_tpl= ()
            order_of_match=-1
            char_list=[]
            result_context_list =[]
            result_sign = ""
            result_score = -1
            result_order = -1
            current_order = -1
            prev_successful_order=-1
            
            for ngram_list_item in text_ngrams_list:
                char_list = []
                #print("ngram_list_item:", ngram_list_item)
                
                """Store off the order of current ngram"""
                current_order = len(ngram_list_item)
                
                if(fetch_all_highest_order_results and current_order<prev_successful_order):
                    """This means we are going doing one order and we had found results for a previous order
                    and it is time to return"""
                    return result_list
                
                char_list= self.get_missing_char_options(ngram_list_item)
                
                
                if(len(char_list)==0): 
                    """No Match"""
                    #print("No match for",ngram_list_item, "moving to the next ngram")
                else:
                    for sign in char_list:
                        if(sign!='<s>'and sign!='</s>'): replaced_sign = f"{sign:03}"
                        else: replaced_sign = sign

                        i = ngram_list_item.index("000") if "000" in ngram_list_item else None

                        if(i==None): 
                            print("No missing char found. Returning")
                            break

                        """copy the list, add the new sign and remove the 000"""
                        new_context_text_token_list = ngram_list_item.copy()

                        new_context_text_token_list.insert(i, replaced_sign)
                        new_context_text_token_list.remove("000")
                        #print("new_context_text_token_list", new_context_text_token_list)

                        """Convert to a string"""
                        context_text=""
                        context_text = ' '.join(str(x) for x in new_context_text_token_list)

                        score = self.get_the_score(context_text)
                        #print("Score for:", context_text, ":", score)
                        score_dict[replaced_sign]=score


                    sorted_score_list = sorted(score_dict.items(),reverse=True, key=lambda x:x[1])

                    #print("Sorted Score --------:", sorted_score_list)
                    #result_sign, ersult_score = self.weighted_score(sorted_score_list)
                
                    order_of_match = len(new_context_text_token_list)
                    """ Since we are going down from higher order to lower order ngram
                    if we find a match, we return"""
                    
                    sign_score_tpl = sorted_score_list[0]
                    if(len(sign_score_tpl)>=1):
                        result_context_list =new_context_text_token_list #this is a list
                        result_sign = sign_score_tpl[0]
                        result_score = sign_score_tpl[1]
                        result_order_of_match = order_of_match
                    
                    result_list.append([result_context_list, result_sign, result_score, result_order_of_match])
                    """Store off the order as prev_order"""
                    prev_successful_order = len(ngram_list_item)
                    
                    if(not fetch_all_highest_order_results): return result_list
                   
                
        except Exception as e:
            print("Exception:", e.__class__, "get_missing_char_selection")
            traceback.print_exc()

        """This means either an exception happened or there was no match for any ngram_list_item"""
        return result_list
  
    
    def get_missing_char_options(self, context_text_token_list):
        
        try:
            list_chars = []
            i=-1
            list_dict_ngrams= []
            k= len(context_text_token_list)
            i = context_text_token_list.index("000") if "000" in context_text_token_list else None
            
            if(i==None): 
                print("No Missing chars.Returning ...")
                return None
            
            """ Get the ngrams of order k+1: This is assuming padding is sent in the text"""
            """ If model order is < k then an empty list is returned"""
            list_dict_ngrams = list(self.model.counts[k+1])
            #print("Input context:", context_text_token_list)
            #print("List of ngrams of order ", k, ":", list_dict_ngrams)
            
            for tpl in list_dict_ngrams:
                """ There won't be any match if number of items in tpl is not same as k """
                """ which will happen if context is longer than order of the model"""
                if(len(tpl)==k):
                    #print("text_list, tpl:", context_text_token_list, tpl)
                    match= True
                    for m in range(0, k):
                        """Skip the missing char index and compare the rest"""
                        if(m!=i and context_text_token_list[m]!=tpl[m]):
                            match = False
                            break
                    if(match): 
                        """Append the i th element of the tuple"""
                        """ Don't match <s> and </s>"""
                        if(tpl[i]!="<s>" and tpl[i]!="</s>"): 
                            #print("######## Matched! Adding",tpl[i])
                            list_chars.append(tpl[i])


                """Do a match and append the matched tpls to list_ngrams"""
        except Exception as e:
            print("Exception:", e.__class__, "get_missing_char_options")
            traceback.print_exc()
        return list_chars

    def weighted_score(self, sorted_score_list):
        try:
            sign_list = []
            score_list = []
            sign =""
            score=-1
            for i in range(0, len(sorted_score_list)):
                sign_score_tpl = sorted_score_list[i]
                sign_list.append(sign_score_tpl[0])
                score_list.append(sign_score_tpl[1])
            tuple1 = tuple(sign_list)
            tuple2 = tuple(score_list)

            random_generator = _random_generator(seed)
            random_generator.random()
            sign = _weighted_choice(tuple1, tuple2, random_generator,)
            i=sign_list.index(sign)
            score = score_list[i]

        except Exception as e:
            print("Exception:", e.__class__, "weighted_score")
            traceback.print_exc()
    
        return sign, score
        
    
    def find_char_by_rank(self,text, random_seed=seed, position=-1):
        
        try:
            alpha1 = 0.2
            alpha2 = 0.2
            alpha3 = 0.6
            rank_dict = defaultdict()

            sign_list = orig_sign_df['id_sign'].tolist()

            orig_text = text
            left_bigram_init_char, right_bigram_term_char,trigram_init_char, trigram_term_char ="","","",""
            quadragram_init_char, quadragram_third_char, quadragram_term_char = "","",""

            #list_tokens = nltk.word_tokenize(text)
            list_tokens = text.split(' ')
            
            last_token_index = len(list_tokens)-1 

            i = list_tokens.index("000")
            if(i>0 and i < last_token_index):
                """Medial character"""
                left_bigram_init_char = list_tokens[i-1]
                right_bigram_term_char = list_tokens[i+1]

                trigram_init_char = list_tokens[i-1]
                trigram_term_char = list_tokens[i+1]
            elif(i==0):
                      
                """Initial character"""
                """ We are using <s> as sentence start pading character"""
                #print("index is zero")
                if(i+1<=last_token_index):
                    left_bigram_init_char = '<s>'
                    right_bigram_term_char = list_tokens[i+1]

                    trigram_init_char = '<s>'
                    trigram_term_char = list_tokens[i+1]
                if(i+2<=last_token_index):
                    quadragram_init_char = '<s>'
                    quadragram_third_char = list_tokens[i+1]
                    quadragram_term_char = list_tokens[i+2]
                    
            else:
                print("No missing characters in text")

        
            # Get the list of bigrams 
            left_bigrams_list = self.get_model_ngrams_list0(left_bigram_init_char, 2,"left_bigram")
            right_bigrams_list = self.get_model_ngrams_list0(right_bigram_term_char,2, "right_bigram")

            trigrams_inp = trigram_init_char + " " + trigram_term_char
            trigrams_list = self.get_model_ngrams_list0(trigrams_inp, 3,"trigram")
            
            if(i+2<=last_token_index):
                quadragram_inp = quadragram_init_char + " " + quadragram_third_char + " " + quadragram_term_char
                quadragrams_list = self.get_model_ngrams_list0(quadragram_inp, 4,"quadragram")

            
            left_bigram_score_dict = self.compute_score(left_bigrams_list, left_bigram_init_char, "", "", "left_bigram")
            right_bigram_score_dict = self.compute_score(right_bigrams_list, right_bigram_term_char, "", "","right_bigram")
            trigram_score_dict = self.compute_score(trigrams_list, trigram_init_char, trigram_term_char, "", "trigram")
            if(i+2<=last_token_index): quadragram_score_dict = self.compute_score(quadragrams_list, quadragram_init_char, quadragram_third_char, quadragram_term_char, "quadragram")

            #print("left_bigram_init_char, left_bigrams_list:",left_bigram_init_char, left_bigrams_list, "\n")
            #print("left_bigram_score_dict:",dict(sorted(left_bigram_score_dict.items(),reverse=True, key=lambda item: item[1])))
            
            #print("right_bigram_term_char, right_bigrams_list:",right_bigram_term_char, right_bigrams_list, "\n")
            #print("right_bigram_score_dict:",dict(sorted(right_bigram_score_dict.items(),reverse=True, key=lambda item: item[1])))
            
            #print("trigram_init_char,trigram_term_char, trigrams_list:",trigram_init_char,trigram_term_char, trigrams_list, "\n")
            #print("trigram_score_dict :",dict(sorted(trigram_score_dict.items(),reverse=True, key=lambda item: item[1])))
            
            #if(i+2<=last_token_index): print("quadragram_init_char, quadragram_third_char, quadragram_term_char, quadragrams_list:",quadragram_init_char,quadragram_third_char, quadragram_term_char, quadragrams_list, "\n")
            #if(i+2<=last_token_index): print("quadragram_score_dict1 :",dict(sorted(quadragram_score_dict.items(),reverse=True, key=lambda item: item[1])))

            # Get the rank for each of the sign in sign list

            # Add the three list and use it
            full_list = left_bigrams_list + right_bigrams_list + trigrams_list
            if(i+2<=last_token_index):full_list = full_list + quadragrams_list
            
            for sign in full_list:
                replaced_sign = f"{sign:03}"

                if replaced_sign in left_bigram_score_dict:
                    score_left_bigram = left_bigram_score_dict[replaced_sign]
                else: score_left_bigram=0

                if replaced_sign in right_bigram_score_dict:
                    score_right_bigram = right_bigram_score_dict[replaced_sign]
                else: score_right_bigram=0

                if replaced_sign in trigram_score_dict:
                    score_trigram = trigram_score_dict[replaced_sign]
                else: score_trigram=0
                    
                if(i+2<=last_token_index):
                    if replaced_sign in quadragram_score_dict:
                        score_quadragram = quadragram_score_dict[replaced_sign]
                    else: score_quadragram=0

                if(i+2<=last_token_index):
                    alpha1 = 0.1
                    alpha2 = 0.1
                    alpha3 = 0.3
                    alpha4 = 0.5
                    rank = alpha1*score_left_bigram  + alpha2*score_right_bigram + alpha3*score_trigram + alpha4*score_quadragram
                else:
                    rank = alpha1*score_left_bigram  + alpha2*score_right_bigram + alpha3*score_trigram
                    
                rank_dict[replaced_sign]=rank

            sorted_rank_list = sorted(rank_dict.items(),reverse=True, key=lambda x:x[1])

            #print("Sorted Rank --------:", sorted_rank_list)
            sign_rank_tpl = sorted_rank_list[0]
        
        except Exception as e:
            print("Exception:", e.__class__, "find_char_by_rank")
            traceback.print_exc()
        
        return sign_rank_tpl[0], sign_rank_tpl[1]
            

In [14]:
#Tokenize the text

# If we need to generate ngrams from it from r to l text, ngrams would be in opposite direction, so
# use reversed text to generate tokenized_text (l to r) and regular text to generate reverse_tokenized_text (r to l)
    
tokenized_text = list(df_train_x[df_train_x.l_to_r_text!=''].l_to_r_text.apply(word_tokenize))
reverse_tokenized_text = list(df_train_x_rev[df_train_x_rev.reversed_text!=''].reversed_text.apply(word_tokenize))


#print("tokenized_text:",tokenized_text)
#print("Rev tokenized_text:",reverse_tokenized_text)

In [15]:
#Check one of the models and play with it
k=4
model_kn = KneserNeyInterpolated(k) #Quadgram model
model_kn_rev = KneserNeyInterpolated(k) # Reverse string, Quadgram model

train_data, padded_sents = padded_everygram_pipeline(k, tokenized_text)
train_data_rev, padded_sents_rev = padded_everygram_pipeline(k, reverse_tokenized_text)

model_kn.fit(train_data, padded_sents)
print(model_kn.vocab)

model_kn_rev.fit(train_data_rev, padded_sents_rev)
print(model_kn_rev.vocab)
      
print(model_kn.vocab.lookup(tokenized_text[0]))
print(model_kn.counts)

text_seed = '390'
num_words=1
context = ['390']

#pickle the model
pickle.dump(model_kn, open('pickle/kn_quad_model.pkl', 'wb'))
pickle.dump(model_kn_rev, open('pickle/kn_rev_quad_model.pkl', 'wb'))

#'l_to_r_text' : "634 368 002 061 717 390"
    
print("count of 390:", model_kn.counts['390'])
print(model_kn.counts[['717']]['390'])
print(model_kn.counts[['368', '002']]['061'])
print(model_kn.counts[['002', '061']]['717'])
print(model_kn.score('390'))
# lm.score("b", ["a"]) what is the chance that “b” is preceded by “a”.
print("---", model_kn.score('390', ['717']))

print(model_kn.score('390', '717'.split()))  # P('390'|'717) Given 717 occurs what is the prob of 390
print(model_kn.score('061', '717'.split()))  # P('740'|'390)
print(model_kn.score('368', '002 061'.split()))  # P('368|'002 061')
print(model_kn.score('002', '0061 717'.split()))

print("Entropy and Perplexity")

test = [('634', '368'), ('002', '061')]
print(model_kn.entropy(test))
print(model_kn.perplexity(test))

<Vocabulary with cutoff=1 unk_label='<UNK>' and 583 items>
<Vocabulary with cutoff=1 unk_label='<UNK>' and 583 items>
('817', '002', '013', '840', '176', '100', '740')
<NgramCounter with 4 ngram orders and 69364 ngrams>
count of 390: 162
1
1
1
0.015064778547755347
--- 0.03720518228382043
0.03720518228382043
0.0003374510394697198
3.173520747364137e-05
0.03860319373305213
Entropy and Perplexity
3.3183998522768086
9.97557396604531


In [16]:
print(models_list_fwd_pentagram[0].vocab)
print(models_list_fwd_pentagram[0].counts)
print(models_list_fwd_pentagram[0].order)
print("count of 390:", models_list_fwd_pentagram[0].counts['390'])
print("count of 850:", models_list_fwd_pentagram[0].counts['850'])

print_train_data_details= False
#If you iterate through this, the iterator is done with and model 
# fitting won't work subsequently
# so set print_train_data_details= False before trying the actual model

if(print_train_data_details):
    for ngramlize_sent in train_data_list_fwd_pentagram[0]:
        print(list(ngramlize_sent))
        print()
    print('#############')
    list(padded_sents_list_fwd_pentagram[0])

<Vocabulary with cutoff=1 unk_label='<UNK>' and 583 items>
<NgramCounter with 5 ngram orders and 101705 ngrams>
5
count of 390: 162
count of 850: 19


## Test the ModelWithFilling

In [17]:
model_wf = ModelWithFilling(model_kn, posNgramModel, True) # Fix this later. Need to create Position Model first

print(model_wf.generate(1, ['867'],42, 10))

samples = model_kn.context_counts(model_kn.vocab.lookup(['899']))
print(samples)


Returning Positional Prob for pos: 10 : 409 for text_seed: ['867']
409
<FreqDist with 0 samples and 0 outcomes>


In [18]:
def pack_list(first_param, second_param, third_param):
    packed_list = []
    
    if(third_param!=-1):
        packed_list.append(third_param)
        
    if(second_param!=-1):
        packed_list.append(second_param)
        
    if(first_param!=-1):
        packed_list.append(first_param)
  
    return packed_list

In [19]:
def get_list_token(initial, j, list_tokens, index_unclear_signs, k,l,m):
    one_before=-1
    two_before=-1
    three_before=-1
    param =[]
    last_token_index = len(list_tokens)-1 
    #print(terminal, j, list_tokens, index_unclear_signs, k,l,m)
    
    try:
        if(initial):     
            # You need to send reverse of the characters
            if(index_unclear_signs[j]+k<=last_token_index):
                one_before = list_tokens[index_unclear_signs[j]+k]

            if(index_unclear_signs[j]+l<=last_token_index):
                two_before = list_tokens[index_unclear_signs[j]+l]
            
            if(index_unclear_signs[j]+m<=last_token_index):
                three_before = list_tokens[index_unclear_signs[j]+m]
                
        else:
            if(index_unclear_signs[j]+k>=0):
                one_before= list_tokens[index_unclear_signs[j]+k]

            if(index_unclear_signs[j]+l>=0):
                two_before = list_tokens[index_unclear_signs[j]+l]
                
            if(index_unclear_signs[j]+m>=0):
                three_before = list_tokens[index_unclear_signs[j]+m]


        param = pack_list(one_before, two_before, three_before)
        
    except Exception as e:
        print("Exception:", e.__class__, "occurred in get_list_token.")
    return param

In [20]:
def get_char_by_position(this_text, position_type):
    char_list = []
    # first split the string into chars
    chars = this_text.split(' ') 
    if(position_type == "Initial"):
        char_list.append(chars[0])
    elif(position_type == "Terminal"):
        char_list.append(chars[len(chars)-1])
    return char_list

#test
print(get_char_by_position('850 000 741 838 798 740 621', "Terminal"))


['621']


In [21]:
print(model_it_bigram_kn.generate(1,get_char_by_position('850 000 741 838 798 740 621', "Terminal"), seed ))
print(model_it_bigram_kn.generate(1,['621'], seed ))

print(get_char_by_position('231 233 804', "Terminal"))

print(model_it_bigram_kn.generate(1,get_char_by_position('231 233 804', "Terminal"), seed ))

817
817
['804']
231


In [22]:
def get_perplexity(model1, k, this_texts, this_tokenized_text,seed):
    try:
        model_wf_1 = ModelWithFilling(model1,posNgramModel, None)
        this_data_list = []
        this_data_list, _= padded_everygram_pipeline(k, this_tokenized_text)
        for i, test in enumerate(this_data_list):
            print("Perplexity( {0}):{1}".format(this_texts[i], model_wf_1.get_model().perplexity(test)))
    except Exception as e:
                print("Exception:", e.__class__, "get_perplexity")
                traceback.print_exc()
                

In [23]:
"""For each of the text with unclear character go through it
    and identify the character"""
def find_unclear_characters(model1, model2, a, fill_using_position, seed): 
    ans=-1
    unclear_chars = []
    full_result_list = []
    first_unclear=0
    
    model_wf_1 = ModelWithFilling(model1,posNgramModel, fill_using_position)
    model_wf_2 = ModelWithFilling(model2,posNgramModel, fill_using_position)
    term = None
    rank_algo_1=-1
    rank_algo_2=-1
    result_list = []
    
    for text in a :
        try:
            #Identify the position of the unclear text and get its immediate neighbors
            list_tokens = text.split(' ')
            
            last_token_index = len(list_tokens)-1  
            index_unclear_signs = []
            param =[]
            param1, param2 = [],[]
            
            for i in range(0, last_token_index+1) :
                    if(list_tokens[i]=='000'):
                        index_unclear_signs.append(i)
                        first_unclear=i

            position_unclear_char = len(list_tokens)- first_unclear
            
            #if(verbose_debug): 
                #print("Text:Index of Unclear signs:", str(text) + ": " + str(index_unclear_signs), "position (RtoL):", position_unclear_char)

            """assuming only one unclear sign in a text. TBD: Extend this later to more than one unclear sign"""
            j=0
            rank_algo_1,rank_algo_2=0,0
            
            if(len(index_unclear_signs)==0):
                """ No Unclear chars"""
                print("!!! No Unclear chars, list_tokens:", list_tokens)
                
            
            if(index_unclear_signs[j]==1):
                """Initial char is missing"""
                
                if(verbose_debug): print("L to R: Initial char is unclear", text)
                param = get_list_token(True, j, list_tokens, index_unclear_signs, 1,2,3)
                 
                if(use_initial_terminal_model):
                    """ Get the Terminal character as a list
                        Pass it to the Initial Terminal Model """
                    term = get_char_by_position(text, "Terminal")
                    ans = model_it_bigram_kn.generate(1,get_char_by_position(text, "Terminal"), seed ) 
                    #print("Text:", text, "Terminal Char:", get_char_by_position(text, "Terminal"), "Answer:", ans)
                else:
                    """This is the algo_1"""
                    #ans_algo_1, rank_algo_1 = model_wf_1.find_char_by_rank(text,random_seed=seed, position=position_unclear_char)
                    #print("Char and rank using algo-1", ans_algo_1, rank_algo_1)
                          
                    ans_algo_1, rank_algo_1, order_of_match_algo_1,result_list = model_wf_1.get_missing_char(text,random_seed=seed,position=position_unclear_char)
                    if(verbose_debug): print("Char, score, order of match using algo-1", ans_algo_1, rank_algo_1, order_of_match_algo_1)
                   

                    """ This is the algo_2"""
                    if(verbose_debug): print( "Sending: ", param , " to generate next char from second model")

                    #Use reverse model
                    ans1, dict1, context = model_wf_2.generate_sent0(1, param , random_seed=seed, position=position_unclear_char)
                    order_of_match_algo_2 = len(context)
                    ans_algo_2, rank_algo_2 = model_wf_2.get_char_and_rank(dict1, None)

                    if(verbose_debug): print("Char, score, order of match using algo-2", ans, rank_algo_2, order_of_match_algo_2)

                    
                if(order_of_match_algo_1>=order_of_match_algo_2):
                    ans = ans_algo_1
                    rank = rank_algo_1
                else:
                    print("Initial: !!!!!! algo_2 is better than algo_1")
                    ans= ans_algo_2
                    rank= rank_algo_2      
                    
                if(verbose_debug): print("Answer:", ans)
                unclear_chars.append(ans)
                full_result_list.append(result_list)

            elif(index_unclear_signs[j]==last_token_index-1):
                """Terminal char is missing"""
                ans_algo_1, rank_algo_1, order_of_match_algo_1= "",-1,-1
                ans_algo_2, rank_algo_2, order_of_match_algo_2 = "", -1, -1
                
                param = get_list_token(False, j, list_tokens, index_unclear_signs, -1,-2,-3)
                if(verbose_debug): print("L to R: Terminal char is unclear", text)
                
                """This is the algo_1"""   
                ans_algo_1, rank_algo_1, order_of_match_algo_1,result_list = model_wf_1.get_missing_char(text,random_seed=seed,position=position_unclear_char)
                if(verbose_debug): print("Char, score, order of match using algo-1", ans_algo_1, rank_algo_1, order_of_match_algo_1)
                   

                try:
                    #ans = model_wf_1.generate_sent(1, param, random_seed=seed, position=position_unclear_char)
                    if(verbose_debug): print("Sending: ", param , " to generate next char from first model")
                    
                    ans1, dict1, context = model_wf_1.generate_sent0(1, param , random_seed=seed, position=position_unclear_char)
                    order_of_match_algo_2 = len(context)
                    ans_algo_2, rank_algo_2 = model_wf_1.get_char_and_rank(dict1, None)

                    if(verbose_debug): print("Char, score, order of match using algo-2", ans, rank_algo_2, order_of_match_algo_2)

                except Exception as e:
                    print("Exception:", e.__class__, "find_unclear_characters:generate_sent0")
                
                if(order_of_match_algo_1>=order_of_match_algo_2):
                    ans = ans_algo_1
                    rank = rank_algo_1
                else:
                    print("Terminal: !!!!!! algo_2 is better than algo_1")
                    ans= ans_algo_2
                    rank= rank_algo_2    

                if(verbose_debug): print("Answer:", ans)
                unclear_chars.append(ans)
                full_result_list.append(result_list)

            else:

                #Not proceeding if more than one char is unclear
                if(len(index_unclear_signs)>1):
                    #print("Many chars are unclear in the text, not able to decipher the text. Moving on ...\n")
                    continue
                    
                """Medial char is missing"""
                
                if(verbose_debug): print("L to R: One of the middle char is unclear", text)
                
                #print("Finding char by algo-1")
                #ans_algo_1, rank_algo_1 = model_wf_1.find_char_by_rank(text,random_seed=seed, position=position_unclear_char)
                #context_length_algo1=3 """Max of Trigram match in algo_1"""
                
                ans_algo_1, rank_algo_1, order_of_match_algo_1,result_list = model_wf_1.get_missing_char(text,random_seed=seed,position=position_unclear_char)
                if(verbose_debug): print("Char, score, order of match using algo-1", ans_algo_1, rank_algo_1, order_of_match_algo_1)
               
                #print("Finding char by algo-2")
                param1 = get_list_token(False,j, list_tokens, index_unclear_signs, -1,-2,-3)
                if(verbose_debug): print("L to R - part-1:", text, "Sending: ", param1 , " to generate next char from first model")
                ans1, dict1, context1 = model_wf_1.generate_sent0(1, param1, random_seed=seed, position=position_unclear_char)           
                
                param2 = get_list_token(True,j, list_tokens, index_unclear_signs, 1,2,3)
                if(verbose_debug): print("L to R - part-2:", text, "Sending: ", param2 , " to generate next char from second model")
                ans2, dict2, context2 = model_wf_2.generate_sent0(1, param2, random_seed=seed, position=position_unclear_char)

                ans_algo_2, rank_algo_2 = model_wf_1.get_char_and_rank(dict1, dict2)
               
    
                """
                if(len(context1)>len(context2)):
                    ans_algo2=ans1
                    context_algo2 = context1
                else:
                    ans_algo2=ans2
                    context_algo2 = context2
                
                if(context_length_algo1>len(context_algo2)):
                    ans = ans_algo_1
                    rank = rank_algo_1
                else:
                    if(verbose_debug):print("!!!!!! algo_2 is better than algo_1",rank_algo_1,rank_algo_2,context1,context2 )
                    ans= ans_algo_2
                    rank= rank_algo_2
                """
                if(order_of_match_algo_1>=len(context2)):
                    ans = ans_algo_1
                    rank = rank_algo_1
                else:
                    print("Terminal: !!!!!! algo_2 is better than algo_1",order_of_match_algo_1,len(context2))
                    ans= ans_algo_2
                    rank= rank_algo_2  
                
                #TBD remove this
                #ans = ans_algo_1
                
                if(verbose_debug): print("Answer:", ans, rank)
                unclear_chars.append(ans)
                full_result_list.append(result_list)
        except Exception as e:
            if(verbose_debug): 
                print("Exception:", e.__class__, "find_unclear_characters.")
                traceback.print_exc()
            
    return  unclear_chars, full_result_list


In [24]:
def get_group_for_sign(id_sign):
    for graph in orig_sign_df[orig_sign_df.id_sign==id_sign].graph :
        return(graph)

In [25]:
def add_answers(text,answer_list, answer, type_unclear_char):
    dict_row = {'text':text, 'len_text':len(text), 'answer':answer, 'type': type_unclear_char}
    answer_list.append(dict_row)

In [26]:
def add_wrong_answers(wrong_answer_list, text, predicted_answer,predicted_answer_group, correct_answer,correct_answer_group, type_unclear_char):
    chars = text.split(' ')
    dict_row = {'text':text, 'len_text':len(chars),'pred_answer':predicted_answer, 'pred_answer_group': predicted_answer_group, 'correct_answer': correct_answer,'correct_answer_group': correct_answer_group, 'type': type_unclear_char}
    wrong_answer_list.append(dict_row)
    

In [27]:
def tabulate_answers(ans, full_result_list, test_list):
    tabulated_answers=[]
    text = ""
    predicted_answer_group =""
    this_ans =""
    i=0
    try:
        for answer in ans:
            this_ans = answer.replace(" ", "")
            text =test3_made_up_list[i] #changed_text
            predicted_answer_group = get_group_for_sign(this_ans)
            dict_row = {'text':text, 'pred_answer':this_ans, 'pred_answer_group': predicted_answer_group, 'other_ans':full_result_list}
            tabulated_answers.append(dict_row)
            i=i+1
    except Exception as e:
            print("Exception:", e.__class__, "tabulate_answers")
            traceback.print_exc()
    return tabulated_answers         

In [28]:
def check_answers(ans, test_correct_answers):

    try:
        beg_hit,ter_hit, med_hit,total_hit=0,0,0,0
        beg_hit_category,ter_hit_category, med_hit_category,total_hit_category=0,0,0,0
        
        beg_count,ter_count,med_count,total_count=0,0,0,0
        
        beg_percent,ter_percent,med_percent,total_percent=0,0,0,0
        beg_percent,ter_percent_category,med_percent_category,total_percent_category=0,0,0,0
        
        wrong_answer_list = []
        
        i=0
        for answers in ans:
            correct_ans = test_correct_answers[i].get('answer')
            correct_ans_type = test_correct_answers[i].get('type')
            correct_ans_text = test_correct_answers[i].get('text')
            
            this_ans =answers.replace(" ", "")
            type_unclear_char = correct_ans_type
            
            # Full Match
            if(this_ans==correct_ans):
                if(type_unclear_char==CONST_INITIAL):
                    beg_hit= beg_hit+1
                    beg_count= beg_count+1
                elif(type_unclear_char==CONST_TERMINAL):
                    ter_hit= ter_hit+1
                    ter_count= ter_count+1
                elif(type_unclear_char==CONST_MEDIAL):
                    med_hit= med_hit+1
                    med_count= med_count+1
                    #TBD Remove these
                    #print("Medial match: this_ans, correct_ans", this_ans,correct_ans)
                    
                total_hit=total_hit+1
                total_count= total_count+1
                
            # Only a Category match
            elif(get_group_for_sign(this_ans)==get_group_for_sign(correct_ans)):
                if(type_unclear_char==CONST_INITIAL):
                    beg_hit_category= beg_hit_category+1
                    beg_count= beg_count+1
                elif(type_unclear_char==CONST_TERMINAL):
                    ter_hit_category= ter_hit_category+1
                    ter_count= ter_count+1
                elif(type_unclear_char==CONST_MEDIAL):
                    med_hit_category= med_hit_category+1
                    med_count= med_count+1
                    #TBD Remove these
                    #print("Medial Category match: this_ans, correct_ans", this_ans,correct_ans)
                    
                total_hit_category=total_hit_category+1
                total_count= total_count+1
                
                # Category match is still wrong, so add it to wrong answers
                add_wrong_answers(wrong_answer_list, correct_ans_text, this_ans, get_group_for_sign(this_ans), correct_ans, get_group_for_sign(correct_ans),type_unclear_char)
            
            #Not any match
            else: 
                if(type_unclear_char==CONST_INITIAL):
                    beg_count= beg_count+1
                elif(type_unclear_char==CONST_TERMINAL):
                    ter_count= ter_count+1
                elif(type_unclear_char==CONST_MEDIAL):
                    med_count= med_count+1
                    
                total_count= total_count+1
                
                add_wrong_answers(wrong_answer_list, correct_ans_text, this_ans, get_group_for_sign(this_ans), correct_ans, get_group_for_sign(correct_ans),type_unclear_char)
                
            i=i+1
        
        if(beg_count>0):
            beg_percent = (beg_hit/beg_count)*100
        else:
            beg_percent = -1
            
        if(beg_count>0):
            beg_percent_category = (beg_hit_category/beg_count)*100
        else:
            beg_percent_category  = -1
            
        
        if(ter_count>0):
            ter_percent = (ter_hit/ter_count)*100
        else:
            ter_percent = -1
            
        if(ter_count>0):
            ter_percent_category = (ter_hit_category/ter_count)*100
        else:
            ter_percent_category = -1
            
            
        if(med_count>0):
            med_percent = (med_hit/med_count)*100
        else:
            med_percent = -1
            
        if(med_count>0):
            med_percent_category  = (med_hit_category /med_count)*100
        else:
            med_percent_category  = -1
            
            
        if(total_count>0):
            total_percent = (total_hit/total_count)*100
        else:
            total_percent = -1
            
        if(total_count>0):
            total_percent_category  = (total_hit_category /total_count)*100
        else:
            total_percent_category  = -1
            
        
    except Exception as e:
            print("Exception:", e.__class__, "in check_answers")
            traceback.print_exc()

    return beg_percent,ter_percent,med_percent,total_percent, beg_percent_category,ter_percent_category,med_percent_category,total_percent_category,wrong_answer_list


## TESTING
1. Test 1: Use random sample of Training data but one character is made unclear: Take a few samples from Training data, make some characters as 000 (unclear). Do it in begining, terminal and medial regions of the text and see if the model is able to figure out the unclear characters
2. Test 2: Use Testing data: Take the Testing data and make some charcters as 000 (unclear). Do it in begining, terminal and medial regions of the text to test and see if the model is able to figure out the unclear characters
3. Test 3: Real Unclear texts: Use the actual texts with unclear data and what the model is able to come up with for the unclear characters

## Test 0 - Manual tests


In [29]:
model_wf_kn = ModelWithFilling(model_kn,posNgramModel, True)
model_wf_kn_rev = ModelWithFilling(model_kn_rev,posNgramModel, True)
#Initial '327 740 090'
print("Train Data: Initial: 327:", model_wf_kn_rev.generate_sent0(1,['740', '772', '240'],8))

#model_wf_kn.get_model_ngrams_list0("<s>", 2,"left_bigram")

#print("Model Counts:", model_wf_kn.get_model().counts[['<s>']]['803'] )
print("Model Prob:", model_wf_kn.get_model().score('240', '<s> 803'.split()))
print("Model Prob:", model_wf_kn.get_model().score('740', '<s> 803 240 772'.split()))

print("Bigram score:", model_wf_kn.get_the_score("<s> 803"))

print("Trigram score:", model_wf_kn.get_the_score("<s> 803"))

#print("Quadragram score:", model_wf_kn.get_the_score("<s> 803 240 772"))

#print("Compute score:", model_wf_kn.compute_score(["803"], "<s>", "240", "172", "quadragram"))

print("-----Train Data: Initial: Ans:803:")
character, rank = model_wf_kn.find_char_by_rank("000 240 772 740", seed)
print(character, rank)

Train Data: Initial: 327: ('0 0 2', defaultdict(None, {'002': 0.3317553272966887, '803': 0.33029968329465553}), ['740', '772', '240'])
Model Prob: 0.06138307221050517
Model Prob: 0.9999206337250176
Bigram score: 0.0029128502561012355
Trigram score: 0.0029128502561012355
-----Train Data: Initial: Ans:803:
803 0.26020022811831334


In [30]:
print("-----Train Data: Initial: Ans:?:")
character, rank = model_wf_kn.find_char_by_rank("000 590 390 741 032 220 440 740", seed)
print(character, rank)

ans1, dict1, context = model_wf_kn_rev.generate_sent0(1,['032', '741', '390', '590'] ,8)
print(ans1, dict1, context)
print(len(context))               

-----Train Data: Initial: Ans:?:
111 0.29959574420006024
0 3 2 defaultdict(None, {'032': 0.46387477017653184}) ['741', '390', '590']
3


In [31]:
#Check one of the models and play with it
k=7
model_kn_sept = KneserNeyInterpolated(k) #sept model
model_kn_sept_rev = KneserNeyInterpolated(k) # Reverse string, Quadgram model

train_data, padded_sents = padded_everygram_pipeline(k, tokenized_text)
train_data_rev, padded_sents_rev = padded_everygram_pipeline(k, reverse_tokenized_text)

model_kn_sept.fit(train_data, padded_sents)
print(model_kn_sept.vocab)

model_kn_sept_rev.fit(train_data_rev, padded_sents_rev)
print(model_kn_sept_rev.vocab)

print(model_kn_sept.counts)

model_wf_kn_sept = ModelWithFilling(model_kn_sept,posNgramModel, True)
model_wf_kn_sept_rev = ModelWithFilling(model_kn_sept_rev,posNgramModel, True)

<Vocabulary with cutoff=1 unk_label='<UNK>' and 583 items>
<Vocabulary with cutoff=1 unk_label='<UNK>' and 583 items>
<NgramCounter with 7 ngram orders and 184387 ngrams>


In [32]:
# 000 740 045  ->(806)

ans1, dict1, context = model_wf_kn_sept.generate_sent0(1,['806', '740'] ,8)
print(ans1, dict1,context)

ans1, dict1, context = model_wf_kn_sept_rev.generate_sent0(1,['045', '740'] ,8)
print(ans1, dict1, context)

print("Score:", model_wf_kn_sept.get_the_score("806 740 045"))

print("Score:", model_wf_kn_sept.get_the_score("222 740 045"))
#ans1, dict1, context = print(model_wf_kn_sept.generate_sent0(1,['740', '045'],8))
#print(ans1, dict1, context)

print("Model Counts of 6:", model_wf_kn_sept.get_model().counts[6])
print("Model Counts of 5:", model_wf_kn_sept.get_model().counts[5])
print("Model Counts of 4:", model_wf_kn_sept.get_model().counts[4])
print("Model Counts of 3:", model_wf_kn_sept.get_model().counts[3])
print("Model Counts of 2:", model_wf_kn_sept.get_model().counts[2])


#print("Values in Model Counts of 5:",list(model_wf_kn_sept.get_model().counts[5]))

context_text_token_list = ['<s>', '740', '045']
#context_text_token_list = ["806", "740", "045"]

print("Score1:", model_wf_kn_sept.get_the_score("<s> 176 740 436 </s>"))
print("Score2:", model_wf_kn_sept.get_model().score('</s>', "176 740 436".split()))

0 6 1 defaultdict(None, {'061': 0.45096767585767317}) ['806', '740']
2 2 0 defaultdict(None, {'001': 0.0038815421162483833, '007': 0.0030017192740666053, '016': 0.006412027162342628, '017': 0.006474871651069898, '031': 0.003975808849339287, '032': 0.010545046670982253, '033': 0.007181872149251684, '035': 0.0030488526406120577, '042': 0.002986008151884788, '048': 0.002986008151884788, '049': 0.0030174303962484227, '050': 0.002986008151884788, '055': 0.00988517953934592, '058': 0.002986008151884788, '060': 0.007087605416160779, '061': 0.00982233505061865, '067': 0.0030174303962484227, '083': 0.002986008151884788, '090': 0.0032059638624302323, '094': 0.002986008151884788, '100': 0.019597636172174013, '101': 0.006317760429251723, '103': 0.0030017192740666053, '140': 0.003535897428248399, '141': 0.002986008151884788, '142': 0.00315883049588478, '143': 0.0030017192740666053, '152': 0.002986008151884788, '158': 0.003064563762793875, '168': 0.00303314151843024, '176': 0.04948913993538552, '180

In [33]:
# Medial various tests

#<s> 220 000 740 090 </s> -> (240)
character, rank = model_wf_kn_sept.find_char_by_rank("<s> 220 000 740 090 </s>", seed)
print("ans", character, "rank", rank)
print("Done finding char by Rank")

#Try forward
print("medial:240 fwd generate_sent", model_wf_kn_sept.generate_sent(1,['<s>'],8))

context = ['<s>', '220', '240']

samples= model_wf_kn_sept.get_model().context_counts(model_wf_kn_sept.get_model().vocab.lookup(context))
print("Context samples-1",samples)
for w in samples:
    print(w, model_wf_kn_sept.get_model().score(w, context) )


context = ['<s>','090', '740', '240']

samples= model_wf_kn_sept_rev.get_model().context_counts(model_wf_kn_sept_rev.get_model().vocab.lookup(context))
print("Context samples-2", samples)

for w in samples:
    print(w, model_wf_kn_sept.get_model().score(w, context) )

    
#Try forward
ans1, dict1, context = model_wf_kn_sept.generate_sent0(1,['<s>', '220'],8)
print("medial:240 fwd","ans", ans1, "dict1", dict1, "context", context)


#Try reverse

ans1, dict1, context = model_wf_kn_sept_rev.generate_sent0(1,['<s>','090', '740'],8)
print("medial:240 rev","ans", ans1, "dict1", dict1, "context", context)


ans 773 rank 0.39886505365930647
Done finding char by Rank
medial:240 fwd generate_sent 1 7 5
Context samples-1 <FreqDist with 1 samples and 1 outcomes>
740 0.9104187512665787
Context samples-2 <FreqDist with 4 samples and 8 outcomes>
235 0.002241271053315516
031 5.7683152057664755e-05
575 1.7042749471582767e-05
220 0.005323547743848166
medial:240 fwd ans 1 4 2 dict1 defaultdict(None, {'017': 0.05134580780690302, '032': 0.05208795738341535, '081': 0.050628766194636944, '100': 0.05204276304777209, '142': 0.05064508637139701, '151': 0.050665172742794015, '176': 0.05344169512235948, '233': 0.05273469669579191, '236': 0.052022676676375085, '240': 0.05274097368685347, '440': 0.05134329701047839, '520': 0.05829276304777209, '550': 0.050655129557095516, '705': 0.05205280623347059, '740': 0.05915668625087878, '798': 0.05343290733487329, '840': 0.05134831860332764}) context ['<s>', '220']
medial:240 rev ans 1 0 3 dict1 defaultdict(None, {'032': 0.04830601053476845, '035': 0.04439642735451147, '

In [34]:
#Medial, Initial, Terminal tests

result_list =[]
print("<s> 220 000 740 090 </s> -> (240)")
      
missing_char, sign_score, order_of_match,result_list= model_wf_kn_sept.get_missing_char("<s> 220 000 740 090 </s>",random_seed=seed, position=-1)
print("-----Medial", missing_char, sign_score, order_of_match)
print()

print("<s> 110 000 </s>  ->(No clear answer)")
missing_char, sign_score, order_of_match,result_list = model_wf_kn_sept.get_missing_char("<s> 110 000 </s>",random_seed=seed, position=-1)
print("-----Medial",missing_char, sign_score, order_of_match)
print()

print("<s> 000 740 045 </s>  ->(806)")
missing_char, sign_score, order_of_match,result_list = model_wf_kn_sept.get_missing_char("<s> 000 740 045 </s>",random_seed=seed, position=-1)
print("-----Initial",missing_char, sign_score, order_of_match)
print()

print("<s>176 740 000 </s> ->(436)")
missing_char, sign_score, order_of_match,result_list = model_wf_kn_sept.get_missing_char("<s> 176 740 000 </s>",random_seed=seed, position=-1)
print("-----Terminal",missing_char, sign_score, order_of_match)
print()

print("<s> 000 </s> ->(Error case - single char)")
missing_char, sign_score, order_of_match,result_list = model_wf_kn_sept.get_missing_char("<s> 000 </s>",random_seed=seed, position=-1)
print("-----Initial/Terminal",missing_char, sign_score, order_of_match)
print()

print("176 740 000 ->(436)")
missing_char, sign_score, order_of_match,result_list = model_wf_kn_sept.get_missing_char("176 740 000",random_seed=seed, position=-1)
print("-----Terminal",missing_char, sign_score, order_of_match)
print()

print("176 740 ->(Error case: No 000)")
missing_char, sign_score, order_of_match,result_list = model_wf_kn_sept.get_missing_char("176 740",random_seed=seed, position=-1)
print("-----?",missing_char, sign_score, order_of_match)
print()

print("<s> 000 032 904 </s> ->(904)")
missing_char, sign_score, order_of_match,result_list = model_wf_kn_sept.get_missing_char("<s> 000 032 904 </s>",random_seed=seed, position=-1)
print("-----Initial",missing_char, sign_score, order_of_match)
print()


<s> 220 000 740 090 </s> -> (240)
-----Medial 240 0.9996112752141902 5

<s> 110 000 </s>  ->(No clear answer)
-----Medial 161 0.9845837099527971 2

<s> 000 740 045 </s>  ->(806)
-----Initial 773 0.9986394352860156 3

<s>176 740 000 </s> ->(436)
-----Terminal 400 0.9994432391206076 4

<s> 000 </s> ->(Error case - single char)
-----Initial/Terminal 161 0.9845837099527971 2

176 740 000 ->(436)
-----Terminal 400 0.13870703430692571 2

176 740 ->(Error case: No 000)
Text does not have missing character!
-----?  -1 -1

<s> 000 032 904 </s> ->(904)
-----Initial 904 0.9306558401124837 4



In [35]:
#print("<s> 000 032 904 </s> ->(904)")
#missing_char, sign_score, order_of_match,result_list = model_wf_kn_sept.get_missing_char("<s> 000 032 904 </s>",random_seed=seed, position=-1)
#print("-----Initial",missing_char, sign_score, order_of_match)
#print()

print("<s> 000 032 740 400 </s>->(028)")
missing_char, sign_score, order_of_match,result_list = model_wf_kn_sept.get_missing_char("<s> 000 032 740 400 </s>",random_seed=seed, position=-1)
print("-----Initial",missing_char, sign_score, order_of_match)
print()


<s> 000 032 740 400 </s>->(028)
-----Initial 027 0.9999721619560304 5



In [36]:
print("-----Testing-------------------")

model_wf_kn = ModelWithFilling(model_kn,posNgramModel, True)
model_wf_kn_rev = ModelWithFilling(model_kn_rev,posNgramModel, True)
    
print("-----RtoL: Terminal char----- Correct Ans: 520")
print("Send three characters")
print(model_wf_kn.generate_sent(1,['060','705', '033'],8))

#ALL OF THIS IS L TO R

#Initial: 741
#741 031 221 400
print("Train Data: Initial: 741:", model_wf_kn_rev.generate_sent(1,['400','221','031'],8))
#-> Not able to find

print("Directly looking")
samples = model_kn_rev.context_counts(model_kn_rev.vocab.lookup(['400','221','031']))
print(samples)
tpl = tuple(model_kn.score(w, context) for w in samples)
for w in samples:
    print(w)
print("tpl:", tpl)

samples = model_kn_rev.context_counts(model_kn_rev.vocab.lookup(['031']))
#print(samples)


#medial: 001
#255 435 690 740 900 001 003 424
print("Train Data: medial: 001:",model_wf_kn.generate_sent(1,['435','690', '740', '900'],8))


#Terminal 740
#321 405 002 806 233 320 920 740
print("Train Data: Terminal 740:", model_wf_kn.generate_sent(1,['233','320', '920'],8))

#Initial: 820
#820 798 740
print("Train Data: Initial: 820:", model_wf_kn_rev.generate_sent(1,['740', '798'],8))

print("Directly looking")
samples = model_kn_rev.context_counts(model_kn_rev.vocab.lookup(['740','798']))
print(samples)
tpl = tuple(model_kn.score(w, context) for w in samples)
for w in samples:
    print(w)
print("tpl:", tpl)


#{'text': '746 130 400', 'len_text': 3, 'pred_answer': '032', 'pred_answer_group': None, 'correct_answer': '746', 'correct_answer_group': 'U-shape', 'type': 'Intial

print("Test Data: Initial: 746:",model_wf_kn_rev.generate_sent(1,['400', '130'],8))
print("Test Data: Initial: 746:",model_wf_kn.generate_sent(1,['130', '400'],8))

print(model_wf_kn.get_the_score("838 798"))
print(model_wf_kn.get_the_score("798 740"))
print(model_wf_kn.get_the_score("838 798 740"))

#medial:798
#850 092 741 838 798 740 621

#Try forward
print("Train Data: medial:798:", model_wf_kn.generate_sent0(1,['092', '741', '838'],8))

#Try reverse
print("Train Data: medial:798:", model_wf_kn_rev.generate_sent0(1,['621', '740'],8))

character =""
print("Finding char by Rank. This will take few min ...")

character, rank = model_wf_kn.find_char_by_rank("850 092 741 838 000 740 621", seed)
print(character, rank)
print("Done finding char by Rank")


-----Testing-------------------
-----RtoL: Terminal char----- Correct Ans: 520
Send three characters
5 2 0
Train Data: Initial: 741: 0 6 0
Directly looking
<FreqDist with 0 samples and 0 outcomes>
tpl: ()
Train Data: medial: 001: 0 0 3
Train Data: Terminal 740: 7 4 0
Train Data: Initial: 820: 2 2 0
Directly looking
<FreqDist with 14 samples and 24 outcomes>
460
220
235
231
233
745
405
838
240
803
002
700
820
003
tpl: (9.824423237744083e-06, 0.0003295258721412967, 1.5870222153278905e-05, 9.068698373302229e-06, 0.000642932928423906, 6.801523779976673e-06, 1.5870222153278905e-05, 3.0228994577674097e-06, 0.0006467115527461153, 0.0003136556499880178, 8.161828535972007e-05, 1.6625947017720754e-05, 0.0003181899991746689, 2.493892052658113e-05)
Test Data: Initial: 746: 7 4 6
Test Data: Initial: 746: </ s>
0.3630423320277192
0.2799993974088581
0.3279999397408858
Train Data: medial:798: ('7 9 8', defaultdict(None, {'798': 0.9336304233202772}), ['092', '741', '838'])
Train Data: medial:798: ('3 9

In [37]:
""" Add initial and terminal padding to each text"""
def pad(text):
    return "<s> " + text + " </s>"

In [38]:
# Function for Data Preparation
# Data preparation for testing
# Take n rows from given set, convert a known sign to unclear sign and produce a dataframe

def prepare_data(a,max_text_chars,min_text_chars,max_num_of_rows, seed):

    list_changed_texts = []
    list_changed_reversed_text = []
    test_correct_answers= []
    row_count=0
    ls_made_up_row = []
    random.seed(seed)

    for text in a:
        """ Tokenize to words, first split the string into chars """
        
        chars = text.split(' ')
        new_text = chars
        #print("text, len(chars),max_text_chars,min_text_chars,row_count",text, len(chars),max_text_chars,min_text_chars,row_count)

        if(len(chars)<=max_text_chars and len(chars)>=min_text_chars) :
            if(len(chars)>=min_text_chars):
                #randomly pick an index in the tokenized_text and change it to unclear
                r = random.randrange(0, len(chars))
            else: r=0

            if(r==0): type_unclear_char = CONST_INITIAL
            elif(r==len(chars)-1): type_unclear_char = CONST_TERMINAL
            else: type_unclear_char = CONST_MEDIAL

            """Pad it in answer and in changed text"""
            add_answers(pad(text), test_correct_answers, chars[r], type_unclear_char)

            new_text[r]= '000'
            # then join with a space
            changed_text = ' '.join((new_text))

            made_up_row= {'site' : 'fake_site',
               'changed_reversed_text'  : pad(reverse_single_text(changed_text)),
               'changed_text' : pad(changed_text)}

            ls_made_up_row.append(made_up_row)


            row_count=row_count+1
            if(row_count>=max_num_of_rows): break


    df_made_up = pd.DataFrame(ls_made_up_row)
    
    return df_made_up, test_correct_answers

In [39]:
def run_model(model_type, model_name_list,model_fwd, model_rev,a, a_rev, seed, fill_using_position, try_reverse, check_the_answers,test_correct_answers, wrong_answer_details_verbose) :
    
    beg_percent,ter_percent,med_percent,total_percent=0,0,0,0
    beg_percent_category,ter_percent_category,med_percent_category,total_percent_category=0,0,0,0
    wrong_answer_list = []
    full_result_list = []
    ans= None
    
    try:
        print("\n_____Trying unclear texts in Fwd Direction:______")
        for index in range(0, len(model_name_list)):

            print("\n****************Model Name:", model_name_list[index], ", Order:", model_fwd[index].order)
            ans,full_result_list = find_unclear_characters(model_fwd[index], model_rev[index],a,fill_using_position, seed)

            print(model_type,":", model_name_list[index])
            if(check_the_answers==True):
                beg_percent,ter_percent,med_percent,total_percent,beg_percent_category,ter_percent_category,med_percent_category,total_percent_category, wrong_answer_list = check_answers(ans,test_correct_answers)

                print("beg%:",round(beg_percent,2), " ter%:",round(ter_percent,2), " med%:", round(med_percent,2), " tot%:", round(total_percent,2)," and a total of ", round((total_percent/100)*len(test_correct_answers)), " out of", len(test_correct_answers))
                
                print("beg_w_cat%:",round(beg_percent+beg_percent_category,2), " ter_w_cat%:",round(ter_percent+ter_percent_category,2), " med_w_cat%:", round(med_percent+med_percent_category,2), " tot_w_cat%:", round(total_percent+total_percent_category,2))
                
                
                if(wrong_answer_details_verbose): print("\n Wrong Answers:", wrong_answer_list)
            else:
                print(tabulate_answers(ans,full_result_list, test3_made_up_list))
                #print("Answers:", ans)
    except Exception as e:
        print("Exception:", e.__class__, "run_model")
        traceback.print_exc()


    if(try_reverse):
        # Try unclear strings in reverse
        print("\n_____Trying unclear texts in Reverse Direction:______")
        try:
            for index in range(0, len(model_name_list)):
                print("\n****************Model Name:", model_name_list[index], ", Order:", model_rev[index].order)
                ans ,full_result_list= find_unclear_characters(model_rev[index], model_fwd[index],a_rev,fill_using_position, seed)

                print(model_type,":", model_name_list[index]) 
                if(check_the_answers==True):
                    beg_percent,ter_percent,med_percent,total_percent, beg_percent_category,ter_percent_category,med_percent_category,total_percent_category, wrong_answer_list = check_answers(ans,test_correct_answers)
                    
                    print(" beg%:",round(beg_percent,2), " ter%:",round(ter_percent,2), " med%:", round(med_percent,2), " tot%:", round(total_percent,2)," and a total of ", round((total_percent/100)*len(test_correct_answers)), " out of", len(test_correct_answers))
                    
                    print("beg_w_cat%:",round(beg_percent+beg_percent_category,2), " ter_w_cat%:",round(ter_percent+ter_percent_category,2), " med_w_cat%:", round(med_percent+med_percent_category,2), " tot_w_cat%:", round(total_percent+total_percent_category,2))
               
                    if(wrong_answer_details_verbose): print("\n Wrong Answers:", wrong_answer_list)
                else:
                    print(tabulate_answers(ans,full_result_list,test3_made_up_list))
                    #print("Answers:", ans)
        except Exception as e:
            print("Exception:", e.__class__, "run_model")
            traceback.print_exc()
    
    return ans



In [40]:
# Function for running a test
def run_test(test_name,data_to_use, a, a_rev,fill_using_position, check_the_answers, test_correct_answers, try_reverse,wrong_answer_details_verbose, seed):
    
    verbose_debug= True
    
    unigram_models= False
    bigram_models= False
    trigram_models= False
    quadgram_models= False
    pentagram_models= False
    hexagram_models= False
    septagram_models= True

    print("_____________________________")
    print("_____ Running ", test_name, "_________")
    print("_____________________________")


    beg_hit,term_hit, med_hit, total_hit=0,0,0,0
    beg_percent,ter_percent,med_percent,total_percent=0,0,0,0
    wrong_answer_list = []

    try_reverse = False

    try:
        if(data_to_use=="all"):
            if(unigram_models):
                ans = run_model("Fwd Unigram Model All:", model_name_list,models_list_fwd_unigram_all, models_list_rev_unigram_all, a, a_rev, seed, fill_using_position, try_reverse, check_the_answers,test_correct_answers, wrong_answer_details_verbose)

            if(bigram_models):
                ans = run_model("Fwd Bigram Model All:", model_name_list,models_list_fwd_bigram_all, models_list_rev_bigram_all, a, a_rev, seed, fill_using_position, try_reverse, check_the_answers,test_correct_answers, wrong_answer_details_verbose)

            if(trigram_models):
                ans = run_model("Fwd Trigram Model All:", model_name_list,models_list_fwd_trigram_all, models_list_rev_trigram_all, a, a_rev, seed, fill_using_position, try_reverse, check_the_answers,test_correct_answers, wrong_answer_details_verbose)

            if(quadgram_models):
                ans = run_model("Fwd Quadgram Model All:", model_name_list,models_list_fwd_quadgram_all, models_list_rev_quadgram_all, a, a_rev, seed, fill_using_position, try_reverse, check_the_answers,test_correct_answers, wrong_answer_details_verbose)

            if(pentagram_models):
                ans = run_model("Fwd Pentagram Model All:", model_name_list,models_list_fwd_pentagram_all, models_list_rev_pentagram_all, a, a_rev, seed, fill_using_position, try_reverse, check_the_answers,test_correct_answers, wrong_answer_details_verbose)

            if(hexagram_models):
                ans = run_model("Fwd hexagram Model All:", model_name_list,models_list_fwd_hexagram_all, models_list_rev_hexagram_all, a, a_rev, seed, fill_using_position, try_reverse, check_the_answers,test_correct_answers, wrong_answer_details_verbose)

            if(septagram_models):
                ans = run_model("Fwd septagram Model All:", model_name_list,models_list_fwd_septagram_all, models_list_rev_septagram_all, a, a_rev, seed, fill_using_position, try_reverse, check_the_answers,test_correct_answers, wrong_answer_details_verbose)
        
        elif(data_to_use=="train"):
            
            if(unigram_models):
                ans = run_model("Fwd Unigram Model Train:", model_name_list,models_list_fwd_unigram, models_list_rev_unigram, a, a_rev, seed, fill_using_position, try_reverse, check_the_answers,test_correct_answers, wrong_answer_details_verbose)

            if(bigram_models):
                ans = run_model("Fwd Bigram Model Train:", model_name_list,models_list_fwd_bigram, models_list_rev_bigram, a, a_rev, seed, fill_using_position, try_reverse, check_the_answers,test_correct_answers, wrong_answer_details_verbose)

            if(trigram_models):
                ans = run_model("Fwd Trigram Model Train:", model_name_list,models_list_fwd_trigram, models_list_rev_trigram, a, a_rev, seed, fill_using_position, try_reverse, check_the_answers,test_correct_answers, wrong_answer_details_verbose)

            if(quadgram_models):
                ans = run_model("Fwd Quadgram Model Train:", model_name_list,models_list_fwd_quadgram, models_list_rev_quadgram, a, a_rev, seed, fill_using_position, try_reverse, check_the_answers,test_correct_answers, wrong_answer_details_verbose)

            if(pentagram_models):
                ans = run_model("Fwd Pentagram Model Train:", model_name_list,models_list_fwd_pentagram, models_list_rev_pentagram, a, a_rev, seed, fill_using_position, try_reverse, check_the_answers,test_correct_answers, wrong_answer_details_verbose)

            if(hexagram_models):
                ans = run_model("Fwd hexagram Model Train:", model_name_list,models_list_fwd_hexagram, models_list_rev_hexagram, a, a_rev, seed, fill_using_position, try_reverse, check_the_answers,test_correct_answers, wrong_answer_details_verbose)

            if(septagram_models):
                ans = run_model("Fwd septagram Model Train:", model_name_list,models_list_fwd_septagram, models_list_rev_septagram, a, a_rev, seed, fill_using_position, try_reverse, check_the_answers,test_correct_answers, wrong_answer_details_verbose)
        else:
            print("Invalid data_to_use. Not proceeding")
            
            
    except Exception as e:
        print("Exception:", e.__class__, "run_test")
        traceback.print_exc()

# Test 1

In [41]:
# Test1
# Data preparation for this test
# Take n rows from train set, convert a known sign to unclear sign and produce a dataframe
# Note down the answers

verbose_debug = True
min_text_chars = 2
max_text_chars = 40
max_num_of_rows= 200
    
df_made_up_from_train, test1_correct_answers =prepare_data(df_train_x[df_train_x.l_to_r_text!=''].l_to_r_text, max_text_chars,min_text_chars,max_num_of_rows, seed)

if(verbose_debug):
    print(df_made_up_from_train.changed_text)
    print(df_made_up_from_train.changed_reversed_text)
    
    print("test1_correct_answers: \n", test1_correct_answers)


0                   <s> 817 000 013 840 176 100 740 </s>
1                               <s> 125 384 000 875 </s>
2      <s> 140 919 520 360 861 002 000 231 705 033 03...
3                                       <s> 000 002 </s>
4                   <s> 032 000 741 350 460 798 740 </s>
                             ...                        
195                         <s> 825 000 495 615 740 </s>
196                                 <s> 235 000 740 </s>
197                                     <s> 180 000 </s>
198                                     <s> 000 740 </s>
199                                     <s> 000 390 </s>
Name: changed_text, Length: 200, dtype: object
0                   <s> 740 100 176 840 013 000 817 </s>
1                               <s> 875 000 384 125 </s>
2      <s> 740 877 032 033 705 231 000 002 861 360 52...
3                                       <s> 002 000 </s>
4                   <s> 740 798 460 350 741 000 032 </s>
                             ...         

In [42]:
# Test1
# Run the test
verbose_debug = False
a= df_made_up_from_train[df_made_up_from_train.changed_text!=''].changed_text
a_rev= df_made_up_from_train[df_made_up_from_train.changed_reversed_text!=''].changed_reversed_text
check_the_answers = True
try_reverse = False
wrong_answer_details_verbose = True
fill_using_position =False
use_initial_terminal_model= False
run_test("Test-1","train",a, a_rev, fill_using_position, check_the_answers, test1_correct_answers, try_reverse, wrong_answer_details_verbose, seed, )
    

_____________________________
_____ Running  Test-1 _________
_____________________________

_____Trying unclear texts in Fwd Direction:______

****************Model Name: MLE , Order: 7
Fwd septagram Model Train: : MLE
beg%: 82.46  ter%: 91.11  med%: 93.88  tot%: 90.0  and a total of  180  out of 200
beg_w_cat%: 84.21  ter_w_cat%: 93.33  med_w_cat%: 94.9  tot_w_cat%: 91.5

 Wrong Answers: [{'text': '<s> 003 140 100 740 </s>', 'len_text': 6, 'pred_answer': '233', 'pred_answer_group': 'fish', 'correct_answer': '140', 'correct_answer_group': 'human', 'type': 'Medial'}, {'text': '<s> 004 390 </s>', 'len_text': 4, 'pred_answer': '728', 'pred_answer_group': 'stick', 'correct_answer': '004', 'correct_answer_group': None, 'type': 'Initial'}, {'text': '<s> 033 700 </s>', 'len_text': 4, 'pred_answer': '032', 'pred_answer_group': None, 'correct_answer': '033', 'correct_answer_group': None, 'type': 'Initial'}, {'text': '<s> 176 740 </s>', 'len_text': 4, 'pred_answer': '156', 'pred_answer_group': 

Fwd septagram Model Train: : Laplace
beg%: 64.91  ter%: 86.67  med%: 95.92  tot%: 85.0  and a total of  170  out of 200
beg_w_cat%: 75.44  ter_w_cat%: 88.89  med_w_cat%: 95.92  tot_w_cat%: 88.5

 Wrong Answers: [{'text': '<s> 818 002 </s>', 'len_text': 4, 'pred_answer': '817', 'pred_answer_group': 'circle', 'correct_answer': '818', 'correct_answer_group': 'circle', 'type': 'Initial'}, {'text': '<s> 005 154 </s>', 'len_text': 4, 'pred_answer': '806', 'pred_answer_group': 'circle', 'correct_answer': '005', 'correct_answer_group': None, 'type': 'Initial'}, {'text': '<s> 235 176 740 </s>', 'len_text': 5, 'pred_answer': '482', 'pred_answer_group': 'A-shape', 'correct_answer': '176', 'correct_answer_group': '-', 'type': 'Medial'}, {'text': '<s> 806 235 520 </s>', 'len_text': 5, 'pred_answer': '240', 'pred_answer_group': 'fish', 'correct_answer': '520', 'correct_answer_group': 'stick', 'type': 'Terminal'}, {'text': '<s> 226 400 </s>', 'len_text': 4, 'pred_answer': '740', 'pred_answer_group': 

Fwd septagram Model Train: : StupidBackoff
beg%: 82.46  ter%: 91.11  med%: 93.88  tot%: 90.0  and a total of  180  out of 200
beg_w_cat%: 84.21  ter_w_cat%: 93.33  med_w_cat%: 94.9  tot_w_cat%: 91.5

 Wrong Answers: [{'text': '<s> 003 140 100 740 </s>', 'len_text': 6, 'pred_answer': '233', 'pred_answer_group': 'fish', 'correct_answer': '140', 'correct_answer_group': 'human', 'type': 'Medial'}, {'text': '<s> 004 390 </s>', 'len_text': 4, 'pred_answer': '728', 'pred_answer_group': 'stick', 'correct_answer': '004', 'correct_answer_group': None, 'type': 'Initial'}, {'text': '<s> 033 700 </s>', 'len_text': 4, 'pred_answer': '032', 'pred_answer_group': None, 'correct_answer': '033', 'correct_answer_group': None, 'type': 'Initial'}, {'text': '<s> 176 740 </s>', 'len_text': 4, 'pred_answer': '156', 'pred_answer_group': 'human', 'correct_answer': '740', 'correct_answer_group': 'U-shape', 'type': 'Terminal'}, {'text': '<s> 700 033 </s>', 'len_text': 4, 'pred_answer': '034', 'pred_answer_group': 

## Test 2

In [43]:
# Test 2
# Data preparation for this test
# Take n rows from test set, convert a known sign to unclear sign and produce a dataframe
# Note down the answers

verbose_debug = True
min_text_chars = 2
max_text_chars = 40
max_num_of_rows=200
    
df_made_up_from_test, test2_correct_answers =prepare_data(df_test_x[df_test_x.l_to_r_text!=''].l_to_r_text, max_text_chars,min_text_chars,max_num_of_rows,seed)

if(verbose_debug):
    print(df_made_up_from_test.changed_text)
    print("test2_correct_answers: \n", test2_correct_answers)


0                          <s> 000 390 </s>
1                      <s> 235 000 520 </s>
2      <s> 861 002 003 000 590 405 740 </s>
3      <s> 140 000 002 415 220 879 740 </s>
4                      <s> 000 703 400 </s>
                       ...                 
195    <s> 603 861 002 032 000 240 520 </s>
196                <s> 861 893 140 000 </s>
197                        <s> 000 592 </s>
198        <s> 000 702 002 240 176 740 </s>
199        <s> 579 250 000 233 803 740 </s>
Name: changed_text, Length: 200, dtype: object
test2_correct_answers: 
 [{'text': '<s> 003 390 </s>', 'len_text': 16, 'answer': '003', 'type': 'Initial'}, {'text': '<s> 235 240 520 </s>', 'len_text': 20, 'answer': '240', 'type': 'Medial'}, {'text': '<s> 861 002 003 220 590 405 740 </s>', 'len_text': 36, 'answer': '220', 'type': 'Medial'}, {'text': '<s> 140 287 002 415 220 879 740 </s>', 'len_text': 36, 'answer': '287', 'type': 'Medial'}, {'text': '<s> 617 703 400 </s>', 'len_text': 20, 'answer': '617', 'type': 

In [44]:
# Test2
# Run the test
verbose_debug = False
a= df_made_up_from_test[df_made_up_from_test.changed_text!=''].changed_text
a_rev= df_made_up_from_test[df_made_up_from_test.changed_reversed_text!=''].changed_reversed_text
check_the_answers = True
try_reverse = False
wrong_answer_details_verbose = True
fill_using_position = False
use_initial_terminal_model= False

ans = run_test("Test-2","train", a, a_rev, fill_using_position, check_the_answers, test2_correct_answers, try_reverse, wrong_answer_details_verbose, seed)

_____________________________
_____ Running  Test-2 _________
_____________________________

_____Trying unclear texts in Fwd Direction:______

****************Model Name: MLE , Order: 7
Fwd septagram Model Train: : MLE
beg%: 12.12  ter%: 34.04  med%: 34.48  tot%: 27.0  and a total of  54  out of 200
beg_w_cat%: 39.39  ter_w_cat%: 40.43  med_w_cat%: 52.87  tot_w_cat%: 45.5

 Wrong Answers: [{'text': '<s> 003 390 </s>', 'len_text': 4, 'pred_answer': '728', 'pred_answer_group': 'stick', 'correct_answer': '003', 'correct_answer_group': None, 'type': 'Initial'}, {'text': '<s> 235 240 520 </s>', 'len_text': 5, 'pred_answer': '231', 'pred_answer_group': 'fish', 'correct_answer': '240', 'correct_answer_group': 'fish', 'type': 'Medial'}, {'text': '<s> 140 287 002 415 220 879 740 </s>', 'len_text': 9, 'pred_answer': '906', 'pred_answer_group': 'bow', 'correct_answer': '287', 'correct_answer_group': 'insect', 'type': 'Medial'}, {'text': '<s> 617 703 400 </s>', 'len_text': 5, 'pred_answer': '060'

Fwd septagram Model Train: : KneserNeyInterpolated
beg%: 12.12  ter%: 36.17  med%: 35.63  tot%: 28.0  and a total of  56  out of 200
beg_w_cat%: 37.88  ter_w_cat%: 44.68  med_w_cat%: 51.72  tot_w_cat%: 45.5

 Wrong Answers: [{'text': '<s> 003 390 </s>', 'len_text': 4, 'pred_answer': '728', 'pred_answer_group': 'stick', 'correct_answer': '003', 'correct_answer_group': None, 'type': 'Initial'}, {'text': '<s> 235 240 520 </s>', 'len_text': 5, 'pred_answer': '231', 'pred_answer_group': 'fish', 'correct_answer': '240', 'correct_answer_group': 'fish', 'type': 'Medial'}, {'text': '<s> 140 287 002 415 220 879 740 </s>', 'len_text': 9, 'pred_answer': '906', 'pred_answer_group': 'bow', 'correct_answer': '287', 'correct_answer_group': 'insect', 'type': 'Medial'}, {'text': '<s> 617 703 400 </s>', 'len_text': 5, 'pred_answer': '060', 'pred_answer_group': None, 'correct_answer': '617', 'correct_answer_group': 'net', 'type': 'Initial'}, {'text': '<s> 031 705 243 </s>', 'len_text': 5, 'pred_answer': '

Fwd septagram Model Train: : Laplace
beg%: 16.67  ter%: 42.55  med%: 42.53  tot%: 34.0  and a total of  68  out of 200
beg_w_cat%: 45.45  ter_w_cat%: 55.32  med_w_cat%: 59.77  tot_w_cat%: 54.0

 Wrong Answers: [{'text': '<s> 235 240 520 </s>', 'len_text': 5, 'pred_answer': '231', 'pred_answer_group': 'fish', 'correct_answer': '240', 'correct_answer_group': 'fish', 'type': 'Medial'}, {'text': '<s> 140 287 002 415 220 879 740 </s>', 'len_text': 9, 'pred_answer': '906', 'pred_answer_group': 'bow', 'correct_answer': '287', 'correct_answer_group': 'insect', 'type': 'Medial'}, {'text': '<s> 617 703 400 </s>', 'len_text': 5, 'pred_answer': '060', 'pred_answer_group': None, 'correct_answer': '617', 'correct_answer_group': 'net', 'type': 'Initial'}, {'text': '<s> 031 705 243 </s>', 'len_text': 5, 'pred_answer': '240', 'pred_answer_group': 'fish', 'correct_answer': '031', 'correct_answer_group': None, 'type': 'Initial'}, {'text': '<s> 806 231 176 740 </s>', 'len_text': 6, 'pred_answer': '233', '

Fwd septagram Model Train: : Lidstone
beg%: 16.67  ter%: 42.55  med%: 42.53  tot%: 34.0  and a total of  68  out of 200
beg_w_cat%: 45.45  ter_w_cat%: 55.32  med_w_cat%: 59.77  tot_w_cat%: 54.0

 Wrong Answers: [{'text': '<s> 235 240 520 </s>', 'len_text': 5, 'pred_answer': '231', 'pred_answer_group': 'fish', 'correct_answer': '240', 'correct_answer_group': 'fish', 'type': 'Medial'}, {'text': '<s> 140 287 002 415 220 879 740 </s>', 'len_text': 9, 'pred_answer': '906', 'pred_answer_group': 'bow', 'correct_answer': '287', 'correct_answer_group': 'insect', 'type': 'Medial'}, {'text': '<s> 617 703 400 </s>', 'len_text': 5, 'pred_answer': '060', 'pred_answer_group': None, 'correct_answer': '617', 'correct_answer_group': 'net', 'type': 'Initial'}, {'text': '<s> 031 705 243 </s>', 'len_text': 5, 'pred_answer': '240', 'pred_answer_group': 'fish', 'correct_answer': '031', 'correct_answer_group': None, 'type': 'Initial'}, {'text': '<s> 806 231 176 740 </s>', 'len_text': 6, 'pred_answer': '233', 

Fwd septagram Model Train: : StupidBackoff
beg%: 12.12  ter%: 34.04  med%: 34.48  tot%: 27.0  and a total of  54  out of 200
beg_w_cat%: 39.39  ter_w_cat%: 40.43  med_w_cat%: 52.87  tot_w_cat%: 45.5

 Wrong Answers: [{'text': '<s> 003 390 </s>', 'len_text': 4, 'pred_answer': '728', 'pred_answer_group': 'stick', 'correct_answer': '003', 'correct_answer_group': None, 'type': 'Initial'}, {'text': '<s> 235 240 520 </s>', 'len_text': 5, 'pred_answer': '231', 'pred_answer_group': 'fish', 'correct_answer': '240', 'correct_answer_group': 'fish', 'type': 'Medial'}, {'text': '<s> 140 287 002 415 220 879 740 </s>', 'len_text': 9, 'pred_answer': '906', 'pred_answer_group': 'bow', 'correct_answer': '287', 'correct_answer_group': 'insect', 'type': 'Medial'}, {'text': '<s> 617 703 400 </s>', 'len_text': 5, 'pred_answer': '060', 'pred_answer_group': None, 'correct_answer': '617', 'correct_answer_group': 'net', 'type': 'Initial'}, {'text': '<s> 031 705 243 </s>', 'len_text': 5, 'pred_answer': '319', 'p

Fwd septagram Model Train: : WittenBellInterpolated
beg%: 13.64  ter%: 42.55  med%: 34.48  tot%: 29.5  and a total of  59  out of 200
beg_w_cat%: 45.45  ter_w_cat%: 53.19  med_w_cat%: 50.57  tot_w_cat%: 49.5

 Wrong Answers: [{'text': '<s> 235 240 520 </s>', 'len_text': 5, 'pred_answer': '231', 'pred_answer_group': 'fish', 'correct_answer': '240', 'correct_answer_group': 'fish', 'type': 'Medial'}, {'text': '<s> 140 287 002 415 220 879 740 </s>', 'len_text': 9, 'pred_answer': '906', 'pred_answer_group': 'bow', 'correct_answer': '287', 'correct_answer_group': 'insect', 'type': 'Medial'}, {'text': '<s> 617 703 400 </s>', 'len_text': 5, 'pred_answer': '060', 'pred_answer_group': None, 'correct_answer': '617', 'correct_answer_group': 'net', 'type': 'Initial'}, {'text': '<s> 031 705 243 </s>', 'len_text': 5, 'pred_answer': '319', 'pred_answer_group': 'net', 'correct_answer': '031', 'correct_answer_group': None, 'type': 'Initial'}, {'text': '<s> 806 231 176 740 </s>', 'len_text': 6, 'pred_ans

## Test 3

In [45]:
# Test 3
# Use the actual unclear text
# We cannot handle multiple unclear character in a single text for now, so discard them
# Data preparation for this test
verbose_debug = True
max_num_of_rows= 100

print("We have", len(df_unclear.index), " rows of unclear texts")

df_made_up = None
ls_made_up_row = []
test3_made_up_list = []
row_count=0

try:
    for text in df_unclear[df_unclear.l_to_r_text!=''].l_to_r_text :
        
        if text.find("[") != -1:
            """ Ignore the row as it is not clear where '[' appears if there is only one sign"""
            continue
        chars = text.split(' ')
        list_index = [i for i,val in enumerate(chars) if val=="000"]
        if(len(list_index)>1):
            print(text, "has more than one unclear char, skipping it ...")
        else:
            """Add this row after update padding for the text and reverse of the text"""
            made_up_row= {'site' : 'fake_site',
               'changed_reversed_text'  : pad(reverse_single_text(text)),
               'changed_text' : pad(text)}
            ls_made_up_row.append(made_up_row)
        
            row_count=row_count+1
            if(row_count>=max_num_of_rows): break

    df_made_up = pd.DataFrame(ls_made_up_row)
    test3_made_up_list  = df_made_up['changed_text'].tolist()
   
    
except Exception as e:
        print("Exception:", e.__class__, "Test 3 : Data preparation")
        traceback.print_exc()
    

if(verbose_debug):
    if(len(df_made_up)>0): 
        print(df_made_up.changed_text)
        print("We have", len(df_made_up.index), " rows of cleaned unclear texts after cleaning up multiple unclear")


We have 291  rows of unclear texts
000 000 233 388 000 has more than one unclear char, skipping it ...
220 803 032 000 000 844 390 031 032 has more than one unclear char, skipping it ...
000 000 000 407 000 900 740 has more than one unclear char, skipping it ...
550 257 002 000 000 has more than one unclear char, skipping it ...
519 740 000 000 has more than one unclear char, skipping it ...
000 060 000 151 has more than one unclear char, skipping it ...
000 000 740 400 has more than one unclear char, skipping it ...
000 000 000 711 400 has more than one unclear char, skipping it ...
000 832 000 740 400 has more than one unclear char, skipping it ...
480 090 000 335 000 has more than one unclear char, skipping it ...
000 000 000 000 220 740 090 has more than one unclear char, skipping it ...
000 000 175 752 740 has more than one unclear char, skipping it ...
000 742 000 390 has more than one unclear char, skipping it ...
000 000 400 has more than one unclear char, skipping it ...
139 0

In [46]:
# Test3
# Run the test
verbose_debug = False
a = df_made_up[df_made_up.changed_text!=''].changed_text
a= df_made_up[df_made_up.changed_reversed_text!=''].changed_reversed_text
try_reverse = False
check_the_answers = False
wrong_answer_details_verbose = False
fill_using_position = False
use_initial_terminal_model= False

ans = run_test("Test-3","all", a, a_rev, fill_using_position, check_the_answers, None, try_reverse, wrong_answer_details_verbose, seed)

_____________________________
_____ Running  Test-3 _________
_____________________________

_____Trying unclear texts in Fwd Direction:______

****************Model Name: MLE , Order: 7
Fwd septagram Model All: : MLE
[{'text': '<s> 000 861 002 503 440 740 </s>', 'pred_answer': '096', 'pred_answer_group': None, 'other_ans': [[[['002', '861', '096', '</s>'], '096', 1.0, 4]], [[['790', '032', '</s>'], '151', 1.0, 3]], [[['<s>', '440', '100'], '415', 0.23809523809523808, 3], [['740', '100', '240'], '740', 1.0, 3]], [[['530', '748', '</s>'], '748', 1.0, 3]], [[['706', '590', '</s>'], '920', 1.0, 3]], [[['<s>', '740', '843'], '690', 0.125, 3]], [[['<s>', '678', '400'], '131', 1.0, 3]], [[['880', '220', '002'], '627', 1.0, 3]], [[['032', '705', '</s>'], '034', 1.0, 3]], [[['<s>', '700', '031', '153'], '153', 1.0, 4], [['031', '850', '032', '</s>'], '153', 1.0, 4]], [[['<s>', '352', '400', '520'], '352', 1.0, 4], [['354', '400', '520', '</s>'], '352', 1.0, 4]], [[['<s>', '556', '817'], '276',

Fwd septagram Model All: : KneserNeyInterpolated
[{'text': '<s> 000 861 002 503 440 740 </s>', 'pred_answer': '096', 'pred_answer_group': None, 'other_ans': [[[['002', '861', '096', '</s>'], '096', 0.9945750225971679, 4]], [[['790', '032', '</s>'], '151', 0.9748472598841686, 3]], [[['<s>', '440', '100'], '440', 0.1833769653956457, 3], [['740', '100', '240'], '740', 0.903020889826253, 3]], [[['530', '748', '</s>'], '748', 0.9907502259716783, 3]], [[['706', '590', '</s>'], '064', 0.958450135583007, 3]], [[['<s>', '740', '843'], '400', 0.05300113821330127, 3]], [[['<s>', '678', '400'], '131', 0.9901687255197349, 3]], [[['880', '220', '002'], '627', 0.9035383607847076, 3]], [[['032', '705', '</s>'], '409', 0.9976875564929195, 3]], [[['<s>', '700', '031', '153'], '153', 0.9450903856583308, 4], [['031', '850', '032', '</s>'], '850', 0.9911050107771109, 4]], [[['<s>', '352', '400', '520'], '352', 0.9905920640572644, 4], [['354', '400', '520', '</s>'], '352', 0.9905920640572644, 4]], [[['<s>',

Fwd septagram Model All: : Laplace
[{'text': '<s> 000 861 002 503 440 740 </s>', 'pred_answer': '096', 'pred_answer_group': None, 'other_ans': [[[['002', '861', '096', '</s>'], '096', 0.003424657534246575, 4]], [[['790', '032', '</s>'], '151', 0.003424657534246575, 3]], [[['<s>', '440', '100'], '415', 0.009933774834437087, 3], [['740', '100', '240'], '415', 0.009933774834437087, 3]], [[['530', '748', '</s>'], '748', 0.003424657534246575, 3]], [[['706', '590', '</s>'], '920', 0.003424657534246575, 3]], [[['<s>', '740', '843'], '690', 0.008130081300813009, 3]], [[['<s>', '678', '400'], '137', 0.006779661016949152, 3]], [[['880', '220', '002'], '455', 0.0068143100511073255, 3]], [[['032', '705', '</s>'], '740', 0.037337662337662336, 3]], [[['<s>', '700', '031', '153'], '153', 0.003424657534246575, 4], [['031', '850', '032', '</s>'], '153', 0.003424657534246575, 4]], [[['<s>', '352', '400', '520'], '352', 0.005128205128205128, 4], [['354', '400', '520', '</s>'], '350', 0.006825938566552901

Fwd septagram Model All: : Lidstone
[{'text': '<s> 000 861 002 503 440 740 </s>', 'pred_answer': '096', 'pred_answer_group': None, 'other_ans': [[[['002', '861', '096', '</s>'], '096', 0.003993154592127781, 4]], [[['790', '032', '</s>'], '151', 0.003993154592127781, 3]], [[['<s>', '440', '100'], '415', 0.012547735951991271, 3], [['740', '100', '240'], '415', 0.012547735951991271, 3]], [[['530', '748', '</s>'], '748', 0.003993154592127781, 3]], [[['706', '590', '</s>'], '920', 0.003993154592127781, 3]], [[['<s>', '740', '843'], '690', 0.010122535961640916, 3]], [[['<s>', '678', '400'], '137', 0.008441193021947102, 3]], [[['880', '220', '002'], '455', 0.0084985835694051, 3]], [[['032', '705', '</s>'], '740', 0.04837852206273259, 3]], [[['<s>', '700', '031', '153'], '153', 0.003993154592127781, 4], [['031', '850', '032', '</s>'], '153', 0.003993154592127781, 4]], [[['<s>', '352', '400', '520'], '352', 0.006260671599317018, 4], [['354', '400', '520', '</s>'], '350', 0.008517887563884156, 4

Fwd septagram Model All: : StupidBackoff
[{'text': '<s> 000 861 002 503 440 740 </s>', 'pred_answer': '096', 'pred_answer_group': None, 'other_ans': [[[['002', '861', '096', '</s>'], '096', 1.0, 4]], [[['790', '032', '</s>'], '151', 1.0, 3]], [[['<s>', '440', '100'], '415', 0.23809523809523808, 3], [['740', '100', '240'], '740', 1.0, 3]], [[['530', '748', '</s>'], '748', 1.0, 3]], [[['706', '590', '</s>'], '920', 1.0, 3]], [[['<s>', '740', '843'], '690', 0.125, 3]], [[['<s>', '678', '400'], '131', 1.0, 3]], [[['880', '220', '002'], '627', 1.0, 3]], [[['032', '705', '</s>'], '034', 1.0, 3]], [[['<s>', '700', '031', '153'], '153', 1.0, 4], [['031', '850', '032', '</s>'], '153', 1.0, 4]], [[['<s>', '352', '400', '520'], '352', 1.0, 4], [['354', '400', '520', '</s>'], '352', 1.0, 4]], [[['<s>', '556', '817'], '276', 1.0, 3]], [[['869', '390', '</s>'], '390', 1.0, 3]], [[['<s>', '740', '923'], '690', 0.125, 3]], [[['<s>', '520', '240'], '220', 0.3333333333333333, 3], [['033', '255', '</s>']

Fwd septagram Model All: : WittenBellInterpolated
[{'text': '<s> 000 861 002 503 440 740 </s>', 'pred_answer': '096', 'pred_answer_group': None, 'other_ans': [[[['002', '861', '096', '</s>'], '096', 0.8588807550786927, 4]], [[['790', '032', '</s>'], '151', 0.8794931721111061, 3]], [[['<s>', '440', '100'], '415', 0.24666143116163286, 3], [['740', '100', '240'], '740', 0.506598396282651, 3]], [[['530', '748', '</s>'], '748', 0.8427615101573853, 3]], [[['706', '590', '</s>'], '064', 0.757071132618039, 3]], [[['<s>', '740', '843'], '690', 0.07447591426756983, 3]], [[['<s>', '678', '400'], '131', 0.7515846757985221, 3]], [[['880', '220', '002'], '627', 0.5180329395103211, 3]], [[['032', '705', '</s>'], '700', 0.9670296203115256, 3]], [[['<s>', '700', '031', '153'], '153', 0.626426076455161, 4], [['031', '850', '032', '</s>'], '850', 0.7915266907604079, 4]], [[['<s>', '352', '400', '520'], '352', 0.8925166560353579, 4], [['354', '400', '520', '</s>'], '350', 0.9094618948967917, 4]], [[['<s>'